# REPORT 2 - Economic considerations of different boosting priority strategies

In this notebook we compute the economic burdens of different age-priority boosting strategies, using the `warwickmodel`, built by Universities of Warwick and Lancaster, with population data from 8 countries with very different socio-economic profiles.

The effectiveness cost of boosters is quantified in terms of reductions in total amount of years of life lost due to boosyer vaccines deploymnet. We assume an initial boosting campaign in the population, with no subsequent boosters being deployed during the simulation. 

The infection dynamics are run for:
 - Dates: **15 Feb 2020** - **25 June 2021**;
 - Countries of interest: **United Kingdom**, **France**;
 - Number of boosters deployed: **10%** of the population.

*The Warwick model is built by Universities of Warwick and Lancaster.*

In [1]:
# Load necessary libraries
import os
import copy
import numpy as np
import pandas as pd
import scipy
import epimodels as em
import warwickmodel as wm
import matplotlib
import plotly.graph_objects as go
from matplotlib import pyplot as plt
from iteration_utilities import deepflatten

## Model Setup
### Define setup matrices for the WarwickLanc Model

In [64]:
np.array(d).shape

(100, 8, 16)

In [67]:
beta[0][0]

[0.6109,
 0.3537,
 0.3998,
 0.4318,
 0.6081,
 0.7004,
 0.7152,
 0.6895,
 0.7075,
 0.766,
 0.8963,
 1.0018,
 1.0455,
 1.307,
 1.387,
 1.415714729541983]

In [2]:
# Populate the model
total_days =  150
regions = ['United Kingdom', 'Canada', 'Brazil', 'South Africa', 'Kenya', 'Philippines', 'Sierra Leone', 'Syria']
age_groups = ['0-4', '5-9', '10-14', '15-19', '20-24', '25-29', '30-34', '35-39',
              '40-44', '45-49', '50-54', '55-59', '60-64', '65-69', '70-74', '75+']

regimes = np.arange(1, 101, 1).tolist()

# Add folder path to data file
path = os.path.join('../data/')

### Read in corresponding data files for the countries considered for all 100 regimes

In [3]:
# Matrices contact
matrices_contact = []
matrices_region = []
time_changes_contact = []
time_changes_region = []

# Vaccine effects
nu_tra = []
nu_symp = []
nu_inf = []
nu_sev_h = []
nu_sev_d = []

# Parameters
omega = []
alpha = []
gamma = []
tau = []
we = []

# Initial conditions
susceptibles_IC = []
exposed1_IC = []
exposed2_IC = []
exposed3_IC = []
exposed4_IC = []
exposed5_IC = []
infectives_sym_IC = []
infectives_asym_IC = []
recovered_IC = []

# Risk factors
d = []
beta = []

# Probabilities of proceeding to severe outcomes
pItoH = []
pHtoD = []

# Distribution of delays before proceeding to severe outcomes
dItoH = []
dHtoD = []

for R in regimes:
        regimes_matrices_region = []

        # Initial state of the system
        weeks_matrices_region = []
        for r in regions:
                region_data_matrix = pd.read_csv(
                        os.path.join(path, '{}/Contacts_{}.csv'.format(r, R)),
                        header=None, dtype=np.float64)
                regional = em.RegionMatrix(r, age_groups, region_data_matrix)
                weeks_matrices_region.append(regional)

        regimes_matrices_region.append(weeks_matrices_region)

        contacts = em.ContactMatrix(age_groups, np.ones((len(age_groups), len(age_groups))))
        regimes_matrices_contact = [contacts]

        matrices_region.append(regimes_matrices_region)
        matrices_contact.append(regimes_matrices_contact)

        # Matrices contact
        time_changes_contact.append([1])
        time_changes_region.append([1])

        # Over 75 population fractions
        frac_pop_over75 = []

        for r in regions:
                IC_df = pd.read_csv(
                        os.path.join(path, '{}/Start_pop_{}.csv'.format(r, R)),
                        skiprows=15,
                        header=None, dtype=np.float64)

                frac_pop_over75.append((1/np.sum(np.asarray(IC_df))) * np.sum(np.asarray(IC_df),axis=1))

        # Risk Factors
        extended_regimes_d = []
        regimes_d = []
        regimes_beta = []

        for r, reg in enumerate(regions):
                RF_df = pd.read_csv(
                        os.path.join(path, '{}/Risks_{}.csv'.format(reg, R)),
                        dtype=np.float64)
                extended_d = RF_df['symptom_risk'].tolist()
                extended_beta = RF_df['susceptibility'].tolist()

                extended_regimes_d.append(extended_d)

                regimes_d.append(extended_d[:15] + [np.sum(np.multiply(extended_d[15:], frac_pop_over75[r]))])
                regimes_beta.append(extended_beta[:15] + [np.sum(np.multiply(extended_beta[15:], frac_pop_over75[r]))])

        d.append(regimes_d)
        beta.append(regimes_beta)

        # Vaccine effects
        eff_df = pd.read_csv(
                os.path.join(path, 'global_parameters/efficacies_{}.csv'.format(R)),
                usecols=range(1,5), dtype=np.float64)

        VE_i = eff_df['Infection_eff']
        VE_s = eff_df['Symptom_eff']
        VE_h = eff_df['Hosp_eff']
        VE_d = eff_df['Death_eff']

        VE_d = np.divide(VE_d-VE_h, 1-VE_h)
        VE_h = np.divide(VE_h-VE_i, 1-VE_i)
        VE_s = np.divide(VE_s-VE_i, 1-VE_i)

        regimes_nu_tra = [1] * 6
        regimes_nu_symp = np.nan_to_num(1 - VE_s).tolist()
        regimes_nu_inf = np.nan_to_num(1 - VE_i).tolist()
        regimes_nu_sev_h = np.nan_to_num(1 - VE_h).tolist()
        regimes_nu_sev_d = np.nan_to_num(1 - VE_d).tolist()

        nu_tra.append(regimes_nu_tra)
        nu_symp.append(regimes_nu_symp)
        nu_inf.append(regimes_nu_inf)
        nu_sev_h.append(regimes_nu_sev_h)
        nu_sev_d.append(regimes_nu_sev_d)

        # Parameters
        param_df = pd.read_csv(
                os.path.join(path, 'global_parameters/parameters_{}.csv'.format(R)),
                dtype=np.float64)

        regimes_omega = param_df['transmission'].tolist()[0]
        regimes_alpha = 1
        regimes_gamma = param_df['recovery'].tolist()[0]
        regimes_tau = param_df['asymptomatic_transmission'].tolist()[0]
        regimes_we = [param_df['waning_rate'].tolist()[0]] * 2 + [0]

        omega.append(regimes_omega)
        alpha.append(regimes_alpha)
        gamma.append(regimes_gamma)
        tau.append(regimes_tau)
        we.append(regimes_we)

        # Initial conditions
        regimes_susceptibles_IC = []
        regimes_exposed1_IC = []
        regimes_exposed2_IC = []
        regimes_exposed3_IC = []
        regimes_exposed4_IC = []
        regimes_exposed5_IC = []
        regimes_infectives_sym_IC = []
        regimes_infectives_asym_IC = []
        regimes_recovered_IC = []

        # Susceptible
        for r in regions:
                IC_df = pd.read_csv(
                        os.path.join(path, '{}/Start_pop_{}.csv'.format(r, R)),
                        usecols=range(0, 5),
                        header=None, dtype=np.float64)

                extended_S = np.asarray(IC_df)
                under_75_S = extended_S[:15, :]
                over_75_S = extended_S[15:, :]
                reduced_S = np.vstack((under_75_S, np.sum(over_75_S, axis=0)))
                regimes_susceptibles_IC.append(
                        reduced_S.flatten('F').tolist() + [0] * len(age_groups))

        # Exposed 1
        for r in regions:
                IC_df = pd.read_csv(
                        os.path.join(path, '{}/Start_pop_{}.csv'.format(r, R)),
                        usecols=range(5, 10),
                        header=None, dtype=np.float64)

                extended_E1 = np.asarray(IC_df)
                under_75_E1 = extended_E1[:15, :]
                over_75_E1 = extended_E1[15:, :]
                reduced_E1 = np.vstack((under_75_E1, np.sum(over_75_E1, axis=0)))
                regimes_exposed1_IC.append(
                        reduced_E1.flatten('F').tolist() + [0] * len(age_groups))

        # Exposed 2
        for r in regions:
                IC_df = pd.read_csv(
                        os.path.join(path, '{}/Start_pop_{}.csv'.format(r, R)),
                        usecols=range(10, 15),
                        header=None, dtype=np.float64)

                extended_E2 = np.asarray(IC_df)
                under_75_E2 = extended_E2[:15, :]
                over_75_E2 = extended_E2[15:, :]
                reduced_E2 = np.vstack((under_75_E2, np.sum(over_75_E2, axis=0)))
                regimes_exposed2_IC.append(
                        reduced_E2.flatten('F').tolist() + [0] * len(age_groups))

        # Exposed 3
        for r in regions:
                IC_df = pd.read_csv(
                        os.path.join(path, '{}/Start_pop_{}.csv'.format(r, R)),
                        usecols=range(15, 20),
                        header=None, dtype=np.float64)

                extended_E3 = np.asarray(IC_df)
                under_75_E3 = extended_E3[:15, :]
                over_75_E3 = extended_E3[15:, :]
                reduced_E3 = np.vstack((under_75_E3, np.sum(over_75_E3, axis=0)))
                regimes_exposed3_IC.append(
                        reduced_E3.flatten('F').tolist() + [0] * len(age_groups))

        # Exposed 4
        for r in regions:
                IC_df = pd.read_csv(
                        os.path.join(path, '{}/Start_pop_{}.csv'.format(r, R)),
                        usecols=range(20, 25),
                        header=None, dtype=np.float64)

                extended_E4 = np.asarray(IC_df)
                under_75_E4 = extended_E4[:15, :]
                over_75_E4 = extended_E4[15:, :]
                reduced_E4 = np.vstack((under_75_E4, np.sum(over_75_E4, axis=0)))
                regimes_exposed4_IC.append(
                        reduced_E4.flatten('F').tolist() + [0] * len(age_groups))

        # Exposed 5
        for r in regions:
                IC_df = pd.read_csv(
                        os.path.join(path, '{}/Start_pop_{}.csv'.format(r, R)),
                        usecols=range(25, 30),
                        header=None, dtype=np.float64)

                extended_E5 = np.asarray(IC_df)
                under_75_E5 = extended_E5[:15, :]
                over_75_E5 = extended_E5[15:, :]
                reduced_E5 = np.vstack((under_75_E5, np.sum(over_75_E5, axis=0)))
                regimes_exposed5_IC.append(
                        reduced_E5.flatten('F').tolist() + [0] * len(age_groups))

        # Symptomatic & Asymptomatic Infectious
        for _, r in enumerate(regions):
                IC_df = pd.read_csv(
                        os.path.join(path, '{}/Start_pop_{}.csv'.format(r, R)),
                        usecols=range(30, 35),
                        header=None, dtype=np.float64)

                extended_I = np.zeros_like(np.asarray(IC_df))
                extended_I[:, 0] = np.matmul(np.diag(regimes_nu_symp[0] * np.array(extended_regimes_d[_])), np.asarray(IC_df)[:, 0])
                extended_I[:, 1] = np.matmul(np.diag(regimes_nu_symp[1] * np.array(extended_regimes_d[_])), np.asarray(IC_df)[:, 1])
                extended_I[:, 2] = np.matmul(np.diag(regimes_nu_symp[2] * np.array(extended_regimes_d[_])), np.asarray(IC_df)[:, 2])
                extended_I[:, 3] = np.matmul(np.diag(regimes_nu_symp[3] * np.array(extended_regimes_d[_])), np.asarray(IC_df)[:, 3])
                extended_I[:, 4] = np.matmul(np.diag(regimes_nu_symp[4] * np.array(extended_regimes_d[_])), np.asarray(IC_df)[:, 4])
                under_75_I = extended_I[:15, :]
                over_75_I = extended_I[15:, :]
                reduced_I = np.vstack((under_75_I, np.sum(over_75_I, axis=0)))
                regimes_infectives_sym_IC.append(
                        reduced_I.flatten('F').tolist() + [0] * len(age_groups))

                extended_A = np.zeros_like(np.asarray(IC_df))
                extended_A[:, 0] = np.matmul(np.diag((1 - regimes_nu_symp[0] * np.array(extended_regimes_d[_]))), np.asarray(IC_df)[:, 0])
                extended_A[:, 1] = np.matmul(np.diag((1 - regimes_nu_symp[1] * np.array(extended_regimes_d[_]))), np.asarray(IC_df)[:, 1])
                extended_A[:, 2] = np.matmul(np.diag((1 - regimes_nu_symp[2] * np.array(extended_regimes_d[_]))), np.asarray(IC_df)[:, 2])
                extended_A[:, 3] = np.matmul(np.diag((1 - regimes_nu_symp[3] * np.array(extended_regimes_d[_]))), np.asarray(IC_df)[:, 3])
                extended_A[:, 4] = np.matmul(np.diag((1 - regimes_nu_symp[4] * np.array(extended_regimes_d[_]))), np.asarray(IC_df)[:, 4])
                under_75_A = extended_A[:15, :]
                over_75_A = extended_A[15:, :]
                reduced_A = np.vstack((under_75_A, np.sum(over_75_A, axis=0)))
                regimes_infectives_asym_IC.append(
                        reduced_A.flatten('F').tolist() + [0] * len(age_groups))

        # Recovered
        for r in regions:
                IC_df = pd.read_csv(
                        os.path.join(path, '{}/Start_pop_{}.csv'.format(r, R)),
                        usecols=[35],
                        header=None, dtype=np.float64)

                extended_R = np.asarray(IC_df)
                under_75_R = extended_R[:15, :]
                over_75_R = extended_R[15:, :]
                reduced_R = np.vstack((under_75_R, np.sum(over_75_R, axis=0)))
                regimes_recovered_IC.append(
                        reduced_R.flatten('F').tolist())

        susceptibles_IC.append(regimes_susceptibles_IC)
        exposed1_IC.append(regimes_exposed1_IC)
        exposed2_IC.append(regimes_exposed2_IC)
        exposed3_IC.append(regimes_exposed3_IC)
        exposed4_IC.append(regimes_exposed4_IC)
        exposed5_IC.append(regimes_exposed5_IC)
        infectives_sym_IC.append(regimes_infectives_sym_IC)
        infectives_asym_IC.append(regimes_infectives_asym_IC)
        recovered_IC.append(regimes_recovered_IC)

        # Set time-to-hospitalisation using a Gamma distribution using the mean and standard deviation 
        th_mean = param_df['hosp_lag'].tolist()[0]+0.00001
        th_var = 12.1**2
        theta = th_var / th_mean
        k = th_mean / theta
        time_to_hosp = scipy.stats.gamma(k, scale=theta).pdf(np.arange(1, 31)).tolist()

        # Set time-to-death using a Gamma distribution using the mean and standard deviation
        td_mean = param_df['death_lag'].tolist()[0]
        td_var = 12.1**2
        theta = td_var / td_mean
        k = td_mean / theta
        time_to_death = scipy.stats.gamma(k, scale=theta).pdf(np.arange(1, 31)).tolist()

        # Probabilities of proceeding to severe outcomes
        # Infected -> Hospital
        extended_pItoH = RF_df['hospitalisation_risk'].tolist()

        regimes_pItoH = []
        for r, reg in enumerate(regions):
                regimes_pItoH.append(extended_pItoH[:15] + [np.sum(np.multiply(extended_pItoH[15:], frac_pop_over75[r]))])

        pItoH.append(regimes_pItoH)

        # Hospital -> Death
        extended_pHtoD = RF_df['death_risk'].tolist()

        regimes_pHtoD = []
        for r, reg in enumerate(regions):
                regimes_pHtoD.append(extended_pHtoD[:15] + [np.sum(np.multiply(extended_pHtoD[15:], frac_pop_over75[r]))])

        pHtoD.append(regimes_pHtoD)

        # Distribution of delays before proceeding to severe outcomes
        # Infected -> Hospital
        dItoH.append(time_to_hosp)
        # Hospital -> Death
        dHtoD.append(time_to_death)

# Other parameters
vac=0
vacb=0

adult = np.ones(len(age_groups))
adult[0] = 0
adult[1] = 0
adult[2] = 0

### Calculate life expectancy for each region

In [4]:
# Read region-dependent vectors of years of life lost
life_ex = []

for r, reg in enumerate(regions):
        # Read life expectancy data
        LE_df = pd.read_csv(os.path.join(path, 'Life_expectancy_{}.csv'.format(reg)),
                usecols=[1, 2], dtype=np.float64)
        LE = np.array(LE_df)

        # Read age & sex distribution data
        ASD_df = pd.read_csv(os.path.join(path, 'Age_sex_distribution_{}.csv'.format(reg)),
                usecols=[1, 2], dtype=np.float64)
        extended_ASD = np.array(ASD_df)
        ASD = np.zeros_like(LE)

        # Group the ages of the ASD into the same age groups as the LE
        sum_ages = [
                0, range(1, 5), range(5, 10), range(10, 15), range(15, 20), range(20, 25), range(25, 30), range(30, 35), range(35, 40), 
                range(40, 45), range(45, 50), range(50, 55), range(55, 60), range(60, 65), range(65, 70), range(70, 75), range(75, 80), 
                range(80, 85), range(85, 101)]

        ASD[0, :] = extended_ASD[sum_ages[0], :]

        for _, ages in enumerate(sum_ages[1:]):
                ASD[_ + 1, :] = np.sum(extended_ASD[ages, :], axis=0)

        frac_ASD = np.matmul(np.diag(1/np.sum(ASD, axis=1)), ASD)

        # Compute the life expectancy of the different age groups
        total_LE = np.sum(np.multiply(frac_ASD, LE), axis=1)

        # Read Life expectancy data
        frac_AD = (1/np.sum(ASD[:2, :]) * np.sum(ASD[:2, :], axis=1)).tolist() + [1] * 14 + (1/np.sum(ASD[16:, :]) * np.sum(ASD[16:, :], axis=1)).tolist()

        # Compute the life expectancy of the correct age groups
        split_LE = np.multiply(frac_AD, total_LE)
        
        final_LE = np.zeros(len(age_groups))
        final_LE[0] = np.sum(split_LE[:2])
        final_LE[1:15] = split_LE[2:16]
        final_LE[15] = np.sum(split_LE[16:]).tolist()

        life_ex.append(final_LE)
      

### Calculate total population for each regime

In [5]:
# Compute the number of boosters for each region
total_pop = []

for R in regimes:
        regimes_total_pop = []
        for r in regions:
                IC_df = pd.read_csv(
                        os.path.join(path, '{}/Start_pop_{}.csv'.format(r, R)),
                        header=None, dtype=np.float64)

                regimes_total_pop.append(np.sum(np.asarray(IC_df)))
        total_pop.append(regimes_total_pop)

## Boosting campaign scenarios

We only boost the partially-waned and recovered. However those in the R compartment who receive the booster do not move out of the compartment (they have higher immunity than the boosted)

In [6]:
# Maximum percentage booster uptake of each age group
boost_age_percent = 0.9

# Compute the maximum number of boosters we can deploy for each age group in each region
max_boosters = []
max_boosters_for_R = []
max_boosters_for_S = []
max_boosters_for_Sf = []
max_boosters_for_Sw1 = []
max_boosters_for_Sw2 = []
max_boosters_for_Sw3 = []

for R, _ in enumerate(regimes):
        regimes_max_boosters = []
        regimes_max_boosters_for_R = []
        regimes_max_boosters_for_S = []
        regimes_max_boosters_for_Sf = []
        regimes_max_boosters_for_Sw1 = []
        regimes_max_boosters_for_Sw2 = []
        regimes_max_boosters_for_Sw3 = []

        for r, reg in enumerate(regions):
                boosters_for_R = boost_age_percent * np.asarray(recovered_IC[R][r])
                boosters_for_S = boost_age_percent * np.asarray(susceptibles_IC[R][r])[:len(age_groups)]
                boosters_for_Sf = boost_age_percent * np.asarray(susceptibles_IC[R][r])[len(age_groups):(2*len(age_groups))]
                boosters_for_Sw1 = boost_age_percent * np.asarray(susceptibles_IC[R][r])[(3*len(age_groups)):(4*len(age_groups))]
                boosters_for_Sw2 = boost_age_percent * np.asarray(susceptibles_IC[R][r])[(4*len(age_groups)):(5*len(age_groups))]
                boosters_for_Sw3 = boost_age_percent * np.asarray(susceptibles_IC[R][r])[(5*len(age_groups)):(6*len(age_groups))]

                regimes_max_boosters_for_R.append(boosters_for_R)
                regimes_max_boosters_for_S.append(boosters_for_S)
                regimes_max_boosters_for_Sf.append(boosters_for_Sf)
                regimes_max_boosters_for_Sw1.append(boosters_for_Sw1)
                regimes_max_boosters_for_Sw2.append(boosters_for_Sw2)
                regimes_max_boosters_for_Sw3.append(boosters_for_Sw3)

                regimes_max_boosters.append(
                        boosters_for_R + boosters_for_S + boosters_for_Sf +
                        boosters_for_Sw1 + boosters_for_Sw2 + boosters_for_Sw3)

        max_boosters_for_R.append(regimes_max_boosters_for_R)
        max_boosters_for_S.append(regimes_max_boosters_for_S)
        max_boosters_for_Sf.append(regimes_max_boosters_for_Sf)
        max_boosters_for_Sw1.append(regimes_max_boosters_for_Sw1)
        max_boosters_for_Sw2.append(regimes_max_boosters_for_Sw2)
        max_boosters_for_Sw3.append(regimes_max_boosters_for_Sw3)
        max_boosters.append(regimes_max_boosters)

# Create list of new susceptible_ICs for each vaccination scenario
scenario_susceptibles_IC = []
scenario_boosted = []
scenario_boost_pop_percent = []
scenario_names = []
age_boosting_scenario_order = []

**Scenario 1**: Prioritising those 75+

In [7]:
scenario_names.append('Prioritise 75+')
age_boosting_scenario_order.append((np.arange(16, 0, -1) - 1).tolist())
scenario_boost_pop_percent.append(0.1)

**Scenario 2**: Prioritising those 60-74 then 75+

In [8]:
scenario_names.append('Prioritise 60-74 then 75+')
age_boosting_scenario_order.append([range(12, 15), 15] + (np.arange(12, 0, -1) - 1).tolist())
scenario_boost_pop_percent.append(0.1)

**Scenario 3**: Prioritising those 60-74 then 50-59, then 75+

In [9]:
scenario_names.append('Prioritise those 60-74 then 50-59, then 75+')
age_boosting_scenario_order.append([range(12, 15), range(10, 12), 15] + (np.arange(10, 0, -1) - 1).tolist())
scenario_boost_pop_percent.append(0.1)

**Scenario 4**: Prioritising those 50-59, then 60-74 then 75+

In [10]:
scenario_names.append('Prioritise those 50-59 then 60-74, then 75+')
age_boosting_scenario_order.append([range(10, 12), range(12, 15), 15] + (np.arange(10, 0, -1) - 1).tolist())
scenario_boost_pop_percent.append(0.1)

**Scenario 5**: Prioritising those 20-49, then 50-74 then 75+

In [11]:
scenario_names.append('Prioritise those 20-49, then 50-74 then 75+')
age_boosting_scenario_order.append([range(4, 10), range(10, 15), 15] + (np.arange(4, 0, -1) - 1).tolist())
scenario_boost_pop_percent.append(0.1)

**Scenario 6**: Prioritising those 20-49, then 75+, then 50-74

In [12]:
scenario_names.append('Prioritise those 20-49, then 75+, then 50-74')
age_boosting_scenario_order.append([range(4, 10), 15, range(10, 15)] + (np.arange(4, 0, -1) - 1).tolist())
scenario_boost_pop_percent.append(0.1)

**Scenario 7**: No boosters

In [13]:
scenario_names.append('No boosters')
age_boosting_scenario_order.append((np.arange(16, 0, -1) - 1).tolist())
scenario_boost_pop_percent.append(0)

### Compute new susceptible conditions based on each boosting scenario

In [14]:
for s, _ in enumerate(scenario_names):
    regimes_new_susceptibles_IC = []
    regimes_boosted = []
    scenario_boosters = (scenario_boost_pop_percent[s] * np.array(total_pop)).tolist()

    for R, _ in enumerate(regimes):
        new_susceptibles_IC = [
            np.array(susceptibles_IC[R][r].copy()).reshape((6, 16)).transpose() for r in range(len(regions))]
        
        new_susceptibles_IC = np.array(new_susceptibles_IC)
        regimes_scenario_boosters = scenario_boosters[R]
        reg_new_susceptibles_IC = []

        boosted = np.zeros_like(new_susceptibles_IC[:, :, 2])

        for r, reg in enumerate(regions):
            for ages in age_boosting_scenario_order[s]:
                if np.sum(max_boosters[R][r][ages]) <= scenario_boosters[R][r]:
                    # Add boosted from the S, Sf, Sw1, Sw2, Sw3 to Sb
                    new_susceptibles_IC[r, ages, 2] += max_boosters[R][r][ages] - max_boosters_for_R[R][r][ages]
                    # Remove boosted from the S
                    new_susceptibles_IC[r, ages, 0] -= max_boosters_for_S[R][r][ages]
                    # Remove boosted from the Sf
                    new_susceptibles_IC[r, ages, 1] -= max_boosters_for_Sf[R][r][ages]
                    # Remove boosted from the Sw1
                    new_susceptibles_IC[r, ages, 3] -= max_boosters_for_Sw1[R][r][ages]
                    # Remove boosted from the Sw2
                    new_susceptibles_IC[r, ages, 4] -= max_boosters_for_Sw2[R][r][ages]
                    # Remove boosted from the Sw3
                    new_susceptibles_IC[r, ages, 5] -= max_boosters_for_Sw3[R][r][ages]
                    # Remove boosted from the S, Sf, Sw1, Sw2, Sw3 and R from total boosters for the scenario
                    scenario_boosters[R][r] -= np.sum(max_boosters[R][r][ages])
                    # Complete boosting vaccination vector
                    boosted[r, ages] = max_boosters[R][r][ages]
                else:
                    # Compute proportion of boosters we have left to give for the age group
                    prop = scenario_boosters[R][r] / np.sum(max_boosters[R][r][ages])
                    # Add boosted from the S, Sf, Sw1, Sw2, Sw3 to Sb
                    new_susceptibles_IC[r, ages, 2] += prop * (max_boosters[R][r][ages] - max_boosters_for_R[R][r][ages])
                    # Remove boosted from the S
                    new_susceptibles_IC[r, ages, 0] -= prop * max_boosters_for_S[R][r][ages]
                    # Remove boosted from the Sf
                    new_susceptibles_IC[r, ages, 1] -= prop * max_boosters_for_Sf[R][r][ages]
                    # Remove boosted from the Sw1
                    new_susceptibles_IC[r, ages, 3] -= prop * max_boosters_for_Sw1[R][r][ages]
                    # Remove boosted from the Sw2
                    new_susceptibles_IC[r, ages, 4] -= prop * max_boosters_for_Sw2[R][r][ages]
                    # Remove boosted from the Sw3
                    new_susceptibles_IC[r, ages, 5] -= prop * max_boosters_for_Sw3[R][r][ages]
                    # Remove boosted from the S, Sf, Sw1, Sw2, Sw3 and R from total boosters for the scenario
                    scenario_boosters[R][r] -= prop * np.sum(max_boosters[R][r][ages])
                    # Complete boosting vaccination vector
                    boosted[r, ages] = prop * max_boosters[R][r][ages]

            reg_new_susceptibles_IC.append(list(deepflatten(new_susceptibles_IC[r].transpose())))

        regimes_new_susceptibles_IC.append(reg_new_susceptibles_IC)
        regimes_boosted.append(boosted)
    scenario_susceptibles_IC.append(regimes_new_susceptibles_IC)
    scenario_boosted.append(regimes_boosted)

### Set the parameters and initial conditions of the model and bundle everything together

In [15]:
# Instantiate model
model = wm.WarwickLancSEIRModel()

# Set the region names, contact and regional data of the model
model.set_regions(regions)
model.set_age_groups(age_groups)

# List of times at which we wish to evaluate the states of the compartments of the model
times = np.arange(1, total_days+1, 1).tolist()

In [16]:
model.read_contact_data(matrices_contact[0], time_changes_contact[0])
model.read_regional_data(matrices_region[0], time_changes_region[0])

# Set regional and time dependent parameters
regional_parameters = wm.RegParameters(
    model=model,
    region_index=1
)

# Set ICs parameters
ICs_parameters = wm.ICs(
    model=model,
    susceptibles_IC=scenario_susceptibles_IC[0][0],
    exposed1_IC=exposed1_IC[0],
    exposed2_IC=exposed2_IC[0],
    exposed3_IC=exposed3_IC[0],
    exposed4_IC=exposed4_IC[0],
    exposed5_IC=exposed5_IC[0],
    infectives_sym_IC=infectives_sym_IC[0],
    infectives_asym_IC=infectives_asym_IC[0],
    recovered_IC=recovered_IC[0]
)

# Set disease-specific parameters
disease_parameters = wm.DiseaseParameters(
    model=model,
    d=d[0][0],
    tau=tau[0],
    we=we[0],
    omega=omega[0]
)

# Set transmission parameters
transmission_parameters = wm.Transmission(
    model=model,
    beta=beta[0][0],
    alpha=alpha[0],
    gamma=gamma[0]
)

# Set other simulation parameters
simulation_parameters = wm.SimParameters(
    model=model,
    method='Radau',
    times=times,
    eps=False
)

# Set vaccination parameters
vaccine_parameters = wm.VaccineParameters(
    model=model,
    vac=vac,
    vacb=vacb,
    adult=adult,
    nu_tra=nu_tra[0],
    nu_symp=nu_symp[0],
    nu_inf=nu_inf[0],
    nu_sev_h=nu_sev_h[0],
    nu_sev_d=nu_sev_d[0],
)

# Set social distancing parameters
soc_dist_parameters = wm.SocDistParameters(
    model=model,
    phi=1
)

# Set all parameters in the controller
parameters = wm.ParametersController(
    model=model,
    regional_parameters=regional_parameters,
    ICs_parameters=ICs_parameters,
    disease_parameters=disease_parameters,
    transmission_parameters=transmission_parameters,
    simulation_parameters=simulation_parameters,
    vaccine_parameters=vaccine_parameters,
    soc_dist_parameters=soc_dist_parameters
)

model.simulate(parameters)

array([[ 0.00000000e+00,  0.00000000e+00,  0.00000000e+00, ...,
         0.00000000e+00,  0.00000000e+00,  0.00000000e+00],
       [ 1.64375240e+02,  1.72527512e+02,  1.65548761e+02, ...,
         1.13005198e+04,  1.13229315e+04,  1.96877471e+04],
       [ 6.51572863e+02,  6.83769263e+02,  6.55188220e+02, ...,
         1.10953103e+04,  1.11149735e+04,  1.92036732e+04],
       ...,
       [ 4.08320648e+04,  3.97176666e+04,  1.84943243e+04, ...,
         2.84855632e+02,  3.22355482e+02, -1.89067481e+02],
       [ 4.11480853e+04,  4.00619615e+04,  1.86169420e+04, ...,
         3.21001839e+02,  3.53278600e+02, -7.30041030e+01],
       [ 4.14557326e+04,  4.03978202e+04,  1.87332395e+04, ...,
         3.54354679e+02,  3.81555073e+02,  3.75165586e+01]])

### Simulate for the regions

In [17]:
# Simulate for all the regions and regimes
outputs = []
total_pop = []

for s, scenario in enumerate(scenario_names):
    scenario_outputs = []
    scenario_total_pop = []
    for R, regime in enumerate(regimes):
        model.read_contact_data(matrices_contact[R], time_changes_contact[R])
        model.read_regional_data(matrices_region[R], time_changes_region[R])

        # Set regional and time dependent parameters
        regional_parameters = wm.RegParameters(
            model=model,
            region_index=1
        )

        # Set ICs parameters
        ICs_parameters = wm.ICs(
            model=model,
            susceptibles_IC=scenario_susceptibles_IC[s][R],
            exposed1_IC=exposed1_IC[R],
            exposed2_IC=exposed2_IC[R],
            exposed3_IC=exposed3_IC[R],
            exposed4_IC=exposed4_IC[R],
            exposed5_IC=exposed5_IC[R],
            infectives_sym_IC=infectives_sym_IC[R],
            infectives_asym_IC=infectives_asym_IC[R],
            recovered_IC=recovered_IC[R]
        )

        # Compute age-dependent population
        scenario_total_pop.append(ICs_parameters.total_population())

        # Set disease-specific parameters
        disease_parameters = wm.DiseaseParameters(
            model=model,
            d=d[R][0],
            tau=tau[R],
            we=we[R],
            omega=omega[R]
        )

        # Set transmission parameters
        transmission_parameters = wm.Transmission(
            model=model,
            beta=beta[R][0],
            alpha=alpha[R],
            gamma=gamma[R]
        )

        # Set other simulation parameters
        simulation_parameters = wm.SimParameters(
            model=model,
            method='Radau',
            times=times,
            eps=False
        )

        # Set vaccination parameters
        vaccine_parameters = wm.VaccineParameters(
            model=model,
            vac=vac,
            vacb=vacb,
            adult=adult,
            nu_tra=nu_tra[R],
            nu_symp=nu_symp[R],
            nu_inf=nu_inf[R],
            nu_sev_h=nu_sev_h[R],
            nu_sev_d=nu_sev_d[R],
        )

        # Set social distancing parameters
        soc_dist_parameters = wm.SocDistParameters(
            model=model,
            phi=1
        )

        # Set all parameters in the controller
        parameters = wm.ParametersController(
            model=model,
            regional_parameters=regional_parameters,
            ICs_parameters=ICs_parameters,
            disease_parameters=disease_parameters,
            transmission_parameters=transmission_parameters,
            simulation_parameters=simulation_parameters,
            vaccine_parameters=vaccine_parameters,
            soc_dist_parameters=soc_dist_parameters
        )

        # Simulate for all the regions
        regimes_outputs = []
        for r, reg in enumerate(regions):
            # List of initial conditions and parameters that characterise the model
            parameters.regional_parameters.region_index = r + 1

            parameters.disease_parameters.d = d[R][r]
            parameters.transmission_parameters.beta = beta[R][r]

            # Simulate using the ODE solver
            regimes_outputs.append(model.simulate(parameters))

        scenario_outputs.append(regimes_outputs)

    outputs.append(scenario_outputs)
    total_pop.append(scenario_total_pop)

outputs = np.array(outputs)

In [17]:
# Simulate for all the regions and regimes
_150_outputs = []
_150_total_pop = []

for s, scenario in enumerate(scenario_names):
    scenario_150_outputs = []
    scenario_150_total_pop = []
    for R, regime in enumerate(regimes):
        model.read_contact_data(matrices_contact[R], time_changes_contact[R])
        model.read_regional_data(matrices_region[R], time_changes_region[R])

        # Set regional and time dependent parameters
        regional_parameters = wm.RegParameters(
            model=model,
            region_index=1
        )

        # Set ICs parameters
        ICs_parameters = wm.ICs(
            model=model,
            susceptibles_IC=scenario_susceptibles_IC[s][R],
            exposed1_IC=exposed1_IC[R],
            exposed2_IC=exposed2_IC[R],
            exposed3_IC=exposed3_IC[R],
            exposed4_IC=exposed4_IC[R],
            exposed5_IC=exposed5_IC[R],
            infectives_sym_IC=infectives_sym_IC[R],
            infectives_asym_IC=infectives_asym_IC[R],
            recovered_IC=recovered_IC[R]
        )

        # Compute age-dependent population
        scenario_150_total_pop.append(ICs_parameters.total_population())

        # Set disease-specific parameters
        disease_parameters = wm.DiseaseParameters(
            model=model,
            d=d[R][0],
            tau=tau[R],
            we=we[R],
            omega=omega[R]
        )

        # Set transmission parameters
        transmission_parameters = wm.Transmission(
            model=model,
            beta=beta[R][0],
            alpha=alpha[R],
            gamma=gamma[R]
        )

        # Set other simulation parameters
        simulation_parameters = wm.SimParameters(
            model=model,
            method='Radau',
            times=np.arange(1, 151, 1).tolist(),
            eps=False
        )

        # Set vaccination parameters
        vaccine_parameters = wm.VaccineParameters(
            model=model,
            vac=vac,
            vacb=vacb,
            adult=adult,
            nu_tra=nu_tra[R],
            nu_symp=nu_symp[R],
            nu_inf=nu_inf[R],
            nu_sev_h=nu_sev_h[R],
            nu_sev_d=nu_sev_d[R],
        )

        # Set social distancing parameters
        soc_dist_parameters = wm.SocDistParameters(
            model=model,
            phi=1
        )

        # Set all parameters in the controller
        parameters = wm.ParametersController(
            model=model,
            regional_parameters=regional_parameters,
            ICs_parameters=ICs_parameters,
            disease_parameters=disease_parameters,
            transmission_parameters=transmission_parameters,
            simulation_parameters=simulation_parameters,
            vaccine_parameters=vaccine_parameters,
            soc_dist_parameters=soc_dist_parameters
        )

        # Simulate for all the regions
        regimes_150_outputs = []
        for r, reg in enumerate(regions):
            # List of initial conditions and parameters that characterise the model
            parameters.regional_parameters.region_index = r + 1

            parameters.disease_parameters.d = d[R][r]
            parameters.transmission_parameters.beta = beta[R][r]

            # Simulate using the ODE solver
            regimes_150_outputs.append(model.simulate(parameters))

        scenario_150_outputs.append(regimes_150_outputs)

    _150_outputs.append(scenario_150_outputs)
    _150_total_pop.append(scenario_150_total_pop)

_150_outputs = np.array(_150_outputs)

In [18]:
# Simulate for all the regions and regimes
_150_no_outbreak_outputs = []
_150_no_outbreak_total_pop = []

for s, scenario in enumerate(scenario_names):
    scenario_150_no_outbreak_outputs = []
    scenario_150_no_outbreak_total_pop = []
    for R, regime in enumerate(regimes):
        model.read_contact_data(matrices_contact[R], time_changes_contact[R])
        model.read_regional_data(matrices_region[R], time_changes_region[R])

        # Set regional and time dependent parameters
        regional_parameters = wm.RegParameters(
            model=model,
            region_index=1
        )

        # Set ICs parameters
        ICs_parameters = wm.ICs(
            model=model,
            susceptibles_IC=scenario_susceptibles_IC[s][R],
            exposed1_IC=exposed1_IC[R],
            exposed2_IC=exposed2_IC[R],
            exposed3_IC=exposed3_IC[R],
            exposed4_IC=exposed4_IC[R],
            exposed5_IC=exposed5_IC[R],
            infectives_sym_IC=infectives_sym_IC[R],
            infectives_asym_IC=infectives_asym_IC[R],
            recovered_IC=recovered_IC[R]
        )

        # Compute age-dependent population
        scenario_150_no_outbreak_total_pop.append(ICs_parameters.total_population())

        # Set disease-specific parameters
        disease_parameters = wm.DiseaseParameters(
            model=model,
            d=d[R][0],
            tau=tau[R],
            we=we[R],
            omega=omega[R]
        )

        # Set transmission parameters
        transmission_parameters = wm.Transmission(
            model=model,
            beta=0,
            alpha=alpha[R],
            gamma=gamma[R]
        )

        # Set other simulation parameters
        simulation_parameters = wm.SimParameters(
            model=model,
            method='Radau',
            times=np.arange(1, 151, 1).tolist(),
            eps=False
        )

        # Set vaccination parameters
        vaccine_parameters = wm.VaccineParameters(
            model=model,
            vac=vac,
            vacb=vacb,
            adult=adult,
            nu_tra=nu_tra[R],
            nu_symp=nu_symp[R],
            nu_inf=nu_inf[R],
            nu_sev_h=nu_sev_h[R],
            nu_sev_d=nu_sev_d[R],
        )

        # Set social distancing parameters
        soc_dist_parameters = wm.SocDistParameters(
            model=model,
            phi=1
        )

        # Set all parameters in the controller
        parameters = wm.ParametersController(
            model=model,
            regional_parameters=regional_parameters,
            ICs_parameters=ICs_parameters,
            disease_parameters=disease_parameters,
            transmission_parameters=transmission_parameters,
            simulation_parameters=simulation_parameters,
            vaccine_parameters=vaccine_parameters,
            soc_dist_parameters=soc_dist_parameters
        )

        # Simulate for all the regions
        regimes_150_no_outbreak_outputs = []
        for r, reg in enumerate(regions):
            # List of initial conditions and parameters that characterise the model
            parameters.regional_parameters.region_index = r + 1

            parameters.disease_parameters.d = d[R][r]
            parameters.transmission_parameters.beta = np.zeros_like(beta[R][r])

            # Simulate using the ODE solver
            regimes_150_no_outbreak_outputs.append(model.simulate(parameters))

        scenario_150_no_outbreak_outputs.append(regimes_150_no_outbreak_outputs)

    _150_no_outbreak_outputs.append(scenario_150_no_outbreak_outputs)
    _150_no_outbreak_total_pop.append(scenario_150_no_outbreak_total_pop)

_150_no_outbreak_outputs = np.array(_150_no_outbreak_outputs)

Run model after no outbreak for 150 days

In [19]:
# Simulate for all the regions and regimes
_300_no_outbreak_outputs = []
_300_no_outbreak_total_pop = []

for s, scenario in enumerate(scenario_names):
    scenario_300_no_outbreak_outputs = []
    scenario_300_no_outbreak_total_pop = []
    for R, regime in enumerate(regimes):
        model.read_contact_data(matrices_contact[R], time_changes_contact[R])
        model.read_regional_data(matrices_region[R], time_changes_region[R])

        # Set regional and time dependent parameters
        regional_parameters = wm.RegParameters(
            model=model,
            region_index=1
        )

        # Set ICs parameters
        ICs_parameters = wm.ICs(
            model=model,
            susceptibles_IC=_150_no_outbreak_outputs[s, R, :, -1, :(6 * len(age_groups))],
            exposed1_IC=np.hstack((
                _150_no_outbreak_outputs[s, R, :, -1, (6 * len(age_groups)):(7 * len(age_groups))],
                _150_no_outbreak_outputs[s, R, :, -1, (11 * len(age_groups)):(12 * len(age_groups))],
                _150_no_outbreak_outputs[s, R, :, -1, (16 * len(age_groups)):(17 * len(age_groups))],
                _150_no_outbreak_outputs[s, R, :, -1, (21 * len(age_groups)):(22 * len(age_groups))],
                _150_no_outbreak_outputs[s, R, :, -1, (26 * len(age_groups)):(27 * len(age_groups))],
                _150_no_outbreak_outputs[s, R, :, -1, (31 * len(age_groups)):(32 * len(age_groups))]
            )),
            exposed2_IC=np.hstack((
                _150_no_outbreak_outputs[s, R, :, -1, (7 * len(age_groups)):(8 * len(age_groups))],
                _150_no_outbreak_outputs[s, R, :, -1, (12 * len(age_groups)):(13 * len(age_groups))],
                _150_no_outbreak_outputs[s, R, :, -1, (17 * len(age_groups)):(18 * len(age_groups))],
                _150_no_outbreak_outputs[s, R, :, -1, (22 * len(age_groups)):(23 * len(age_groups))],
                _150_no_outbreak_outputs[s, R, :, -1, (27 * len(age_groups)):(28 * len(age_groups))],
                _150_no_outbreak_outputs[s, R, :, -1, (32 * len(age_groups)):(33 * len(age_groups))]
            )),
            exposed3_IC=np.hstack((
                _150_no_outbreak_outputs[s, R, :, -1, (8 * len(age_groups)):(9 * len(age_groups))],
                _150_no_outbreak_outputs[s, R, :, -1, (13 * len(age_groups)):(14 * len(age_groups))],
                _150_no_outbreak_outputs[s, R, :, -1, (18 * len(age_groups)):(19 * len(age_groups))],
                _150_no_outbreak_outputs[s, R, :, -1, (23 * len(age_groups)):(24 * len(age_groups))],
                _150_no_outbreak_outputs[s, R, :, -1, (28 * len(age_groups)):(29 * len(age_groups))],
                _150_no_outbreak_outputs[s, R, :, -1, (33 * len(age_groups)):(34 * len(age_groups))]
            )),
            exposed4_IC=np.hstack((
                _150_no_outbreak_outputs[s, R, :, -1, (9 * len(age_groups)):(10 * len(age_groups))],
                _150_no_outbreak_outputs[s, R, :, -1, (14 * len(age_groups)):(15 * len(age_groups))],
                _150_no_outbreak_outputs[s, R, :, -1, (19 * len(age_groups)):(20 * len(age_groups))],
                _150_no_outbreak_outputs[s, R, :, -1, (24 * len(age_groups)):(25 * len(age_groups))],
                _150_no_outbreak_outputs[s, R, :, -1, (29 * len(age_groups)):(30 * len(age_groups))],
                _150_no_outbreak_outputs[s, R, :, -1, (34 * len(age_groups)):(35 * len(age_groups))]
            )),
            exposed5_IC=np.hstack((
                _150_no_outbreak_outputs[s, R, :, -1, (10 * len(age_groups)):(11 * len(age_groups))],
                _150_no_outbreak_outputs[s, R, :, -1, (15 * len(age_groups)):(16 * len(age_groups))],
                _150_no_outbreak_outputs[s, R, :, -1, (20 * len(age_groups)):(21 * len(age_groups))],
                _150_no_outbreak_outputs[s, R, :, -1, (25 * len(age_groups)):(26 * len(age_groups))],
                _150_no_outbreak_outputs[s, R, :, -1, (30 * len(age_groups)):(31 * len(age_groups))],
                _150_no_outbreak_outputs[s, R, :, -1, (35 * len(age_groups)):(36 * len(age_groups))]
            )),
            infectives_sym_IC=_150_no_outbreak_outputs[s, R, :, -1, (36 * len(age_groups)):(42 * len(age_groups))],
            infectives_asym_IC=_150_no_outbreak_outputs[s, R, :, -1, (42 * len(age_groups)):(48 * len(age_groups))],
            recovered_IC=_150_no_outbreak_outputs[s, R, :, -1, (48 * len(age_groups)):(49 * len(age_groups))]
        )

        # Compute age-dependent population
        scenario_300_no_outbreak_total_pop.append(ICs_parameters.total_population())

        # Set disease-specific parameters
        disease_parameters = wm.DiseaseParameters(
            model=model,
            d=d[R][0],
            tau=tau[R],
            we=we[R],
            omega=omega[R]
        )

        # Set transmission parameters
        transmission_parameters = wm.Transmission(
            model=model,
            beta=beta[R][r],
            alpha=alpha[R],
            gamma=gamma[R]
        )

        # Set other simulation parameters
        simulation_parameters = wm.SimParameters(
            model=model,
            method='Radau',
            times=np.arange(1, 151, 1).tolist(),
            eps=False
        )

        # Set vaccination parameters
        vaccine_parameters = wm.VaccineParameters(
            model=model,
            vac=vac,
            vacb=vacb,
            adult=adult,
            nu_tra=nu_tra[R],
            nu_symp=nu_symp[R],
            nu_inf=nu_inf[R],
            nu_sev_h=nu_sev_h[R],
            nu_sev_d=nu_sev_d[R],
        )

        # Set social distancing parameters
        soc_dist_parameters = wm.SocDistParameters(
            model=model,
            phi=1
        )

        # Set all parameters in the controller
        parameters = wm.ParametersController(
            model=model,
            regional_parameters=regional_parameters,
            ICs_parameters=ICs_parameters,
            disease_parameters=disease_parameters,
            transmission_parameters=transmission_parameters,
            simulation_parameters=simulation_parameters,
            vaccine_parameters=vaccine_parameters,
            soc_dist_parameters=soc_dist_parameters
        )

        # Simulate for all the regions
        regimes_300_no_outbreak_outputs = []
        for r, reg in enumerate(regions):
            # List of initial conditions and parameters that characterise the model
            parameters.regional_parameters.region_index = r + 1

            parameters.disease_parameters.d = d[R][r]
            parameters.transmission_parameters.beta = beta[R][r]

            # Simulate using the ODE solver
            regimes_300_no_outbreak_outputs.append(model.simulate(parameters))

        scenario_300_no_outbreak_outputs.append(regimes_300_no_outbreak_outputs)

    _300_no_outbreak_outputs.append(scenario_300_no_outbreak_outputs)
    _300_no_outbreak_total_pop.append(scenario_300_no_outbreak_total_pop)

_300_no_outbreak_outputs = np.array(_300_no_outbreak_outputs)

## Save the model output data

In [20]:
# Save output as a numpy matrix file
# np.save('outputs/priority_economic_output', outputs.reshape(-1))
# np.save('outputs/priority_economic_total_pop', total_pop)

np.save('outputs/150_no_outbreak_economic_output', _150_no_outbreak_outputs.reshape(-1))
np.save('outputs/150_no_outbreak_economic_total_pop', _150_no_outbreak_total_pop)

np.save('outputs/300_no_outbreak_economic_output', _300_no_outbreak_outputs.reshape(-1))
np.save('outputs/300_no_outbreak_economic_total_pop', _300_no_outbreak_total_pop)

## Reload model output data

In [21]:
output_format = (len(scenario_names), len(regimes), len(regions), len(times), 50 * len(age_groups))
_150_output_format = (len(scenario_names), len(regimes), len(regions), 150, 50 * len(age_groups))
total_pop_format = (len(scenario_names), len(regimes), len(regions), len(age_groups))

outputs = np.load('outputs/priority_economic_output.npy').reshape(output_format)
total_pop = np.load('outputs/priority_economic_total_pop.npy').reshape(total_pop_format).tolist()

_150_no_outbreak_outputs = np.load('outputs/150_no_outbreak_economic_output.npy').reshape(_150_output_format)
_150_no_outbreak_total_pop = np.load('outputs/150_no_outbreak_economic_total_pop.npy').reshape(total_pop_format).tolist()

_300_no_outbreak_outputs = np.load('outputs/300_no_outbreak_economic_output.npy').reshape(_150_output_format)
_300_no_outbreak_total_pop = np.load('outputs/300_no_outbreak_economic_total_pop.npy').reshape(total_pop_format).tolist()

## Plot the comparments of the two methods against each other
### Setup ``plotly`` and default settings for plotting

In [22]:
from plotly.subplots import make_subplots

colours = ['blue', 'orange', 'green', 'red', 'purple', 'deepskyblue', 'black', 'pink']
cb_colours = ['#FFDD00', '#DC267F', '#648FFF', '#FE6100', '#25E57A', '#785EF0', '#011119']

## Number of New Infections, Hospitalisations, Deaths & Total number of years of life lost

In [23]:
# Simulate for all the regions (sum over all age groups)
total_years_of_life_lost = []
total_boosted = []

for s, scenario in enumerate(scenario_names):
    scenario_total_years_of_life_lost = []
    scenario_total_boosted = []
    for R, regime in enumerate(regimes):
        regimes_total_years_of_life_lost = []
        regimes_boosted = []

        model.vaccine_param[6] = nu_sev_h[R]
        model.vaccine_param[7] = nu_sev_d[R]
        for r, reg in enumerate(regions):
            # Compute regional matrix of new infections for all timepoints simulated
            reg_new_infections = model.new_infections(outputs[s, R, r, :, :])

            # Compute regional matrix of new hospitalisation for all timepoints simulated
            reg_new_hospitalisation = model.new_hospitalisations(reg_new_infections, pItoH[R][r], dItoH[R])

            # Compute regional matrix of new deaths for all timepoints simulated
            reg_new_deaths = model.new_deaths(reg_new_hospitalisation, pHtoD[R][r], dHtoD[R])

            regimes_total_years_of_life_lost.append((10**5) / np.sum(total_pop[s][R][r]) * np.sum(np.matmul(
                reg_new_deaths[0] + reg_new_deaths[1] + reg_new_deaths[2] +
                reg_new_deaths[3] + reg_new_deaths[4] + reg_new_deaths[5],
                np.diag(life_ex[r])), axis=1))

            regimes_boosted.append((10**5) / np.sum(total_pop[s][R][r]) * np.array(scenario_boosted[s][R][r]))

        scenario_total_years_of_life_lost.append(regimes_total_years_of_life_lost)
        scenario_total_boosted.append(regimes_boosted)
    
    total_years_of_life_lost.append(scenario_total_years_of_life_lost)
    total_boosted.append(scenario_total_boosted)

total_years_of_life_lost = np.array(total_years_of_life_lost)
total_boosted = np.array(total_boosted)

total_cum_years_of_life_lost = np.cumsum(total_years_of_life_lost, axis=-1)

In [24]:
# Simulate for all the regions (sum over all age groups)
total_reduction_to_s1_cum_years_of_life_lost = []
total_reduction_to_s7_cum_years_of_life_lost = []

for s, scenario in enumerate(scenario_names):
    scenario_total_reduction_to_s1_cum_years_of_life_lost = []
    scenario_total_reduction_to_s7_cum_years_of_life_lost = []
    for R, regime in enumerate(regimes):
        regimes_total_reduction_to_s1_cum_years_of_life_lost = []
        regimes_total_reduction_to_s7_cum_years_of_life_lost = []

        model.vaccine_param[6] = nu_sev_h[R]
        model.vaccine_param[7] = nu_sev_d[R]
        for r, reg in enumerate(regions):
            # Compute regional matrix of new infections for all timepoints simulated
            reg_new_infections = model.new_infections(outputs[s, R, r, :, :])

            regimes_total_reduction_to_s1_cum_years_of_life_lost.append(100 * np.divide(
                total_cum_years_of_life_lost[s, R, r, :] - total_cum_years_of_life_lost[0, R, r, :],
                total_cum_years_of_life_lost[0, R, r, :])
            )
            regimes_total_reduction_to_s7_cum_years_of_life_lost.append(100 * np.divide(
                total_cum_years_of_life_lost[-1, R, r, :] - total_cum_years_of_life_lost[s, R, r, :],
                total_cum_years_of_life_lost[-1, R, r, :])
            )

        scenario_total_reduction_to_s1_cum_years_of_life_lost.append(regimes_total_reduction_to_s1_cum_years_of_life_lost)
        scenario_total_reduction_to_s7_cum_years_of_life_lost.append(regimes_total_reduction_to_s7_cum_years_of_life_lost)
    
    total_reduction_to_s1_cum_years_of_life_lost.append(scenario_total_reduction_to_s1_cum_years_of_life_lost)
    total_reduction_to_s7_cum_years_of_life_lost.append(scenario_total_reduction_to_s7_cum_years_of_life_lost)

total_reduction_to_s1_cum_years_of_life_lost = np.array(total_reduction_to_s1_cum_years_of_life_lost)
total_reduction_to_s7_cum_years_of_life_lost = np.array(total_reduction_to_s7_cum_years_of_life_lost)

In [25]:
# Simulate for all the regions (sum over all age groups)
model._times = np.arange(1, 151, 1)

_150_no_outbreak_total_deaths = []
_300_no_outbreak_total_deaths = []

_150_no_outbreak_total_years_of_life_lost = []
_300_no_outbreak_total_years_of_life_lost = []

for s, scenario in enumerate(scenario_names):
    scenario_150_no_outbreak_total_deaths = []
    scenario_300_no_outbreak_total_deaths = []

    scenario_150_no_outbreak_total_years_of_life_lost = []
    scenario_300_no_outbreak_total_years_of_life_lost = []
    for R, regime in enumerate(regimes):
        regimes_150_no_outbreak_total_deaths = []
        regimes_300_no_outbreak_total_deaths = []

        regimes_150_no_outbreak_total_years_of_life_lost = []
        regimes_300_no_outbreak_total_years_of_life_lost = []

        model.vaccine_param[6] = nu_sev_h[R]
        model.vaccine_param[7] = nu_sev_d[R]
        for r, reg in enumerate(regions):
            # Compute regional matrix of new infections for all timepoints simulated
            _150_reg_new_infections = model.new_infections(_150_no_outbreak_outputs[s, R, r, :, :])
            _300_reg_new_infections = model.new_infections(_300_no_outbreak_outputs[s, R, r, :, :])

            # Compute regional matrix of new hospitalisation for all timepoints simulated
            _150_reg_new_hospitalisation = model.new_hospitalisations(_150_reg_new_infections, pItoH[R][r], dItoH[R])
            _300_reg_new_hospitalisation = model.new_hospitalisations(_300_reg_new_infections, pItoH[R][r], dItoH[R])

            # Compute regional matrix of new deaths for all timepoints simulated
            _150_reg_new_deaths = model.new_deaths(_150_reg_new_hospitalisation, pHtoD[R][r], dHtoD[R])
            _300_reg_new_deaths = model.new_deaths(_300_reg_new_hospitalisation, pHtoD[R][r], dHtoD[R])

            regimes_150_no_outbreak_total_deaths.append((10**5) / np.sum(_150_no_outbreak_total_pop[s][R][r]) * np.sum(
                _150_reg_new_deaths[0] + _150_reg_new_deaths[1] + _150_reg_new_deaths[2] +
                _150_reg_new_deaths[3] + _150_reg_new_deaths[4] + _150_reg_new_deaths[5],
                axis=1))
            
            regimes_150_no_outbreak_total_years_of_life_lost.append((10**5) / np.sum(_150_no_outbreak_total_pop[s][R][r]) * np.sum(np.matmul(
                _150_reg_new_deaths[0] + _150_reg_new_deaths[1] + _150_reg_new_deaths[2] +
                _150_reg_new_deaths[3] + _150_reg_new_deaths[4] + _150_reg_new_deaths[5],
                np.diag(life_ex[r])), axis=1))

            regimes_300_no_outbreak_total_deaths.append((10**5) / np.sum(_300_no_outbreak_total_pop[s][R][r]) * np.sum(
                _300_reg_new_deaths[0] + _300_reg_new_deaths[1] + _300_reg_new_deaths[2] +
                _300_reg_new_deaths[3] + _300_reg_new_deaths[4] + _300_reg_new_deaths[5],
                axis=1))
            
            regimes_300_no_outbreak_total_years_of_life_lost.append((10**5) / np.sum(_300_no_outbreak_total_pop[s][R][r]) * np.sum(np.matmul(
                _300_reg_new_deaths[0] + _300_reg_new_deaths[1] + _300_reg_new_deaths[2] +
                _300_reg_new_deaths[3] + _300_reg_new_deaths[4] + _300_reg_new_deaths[5],
                np.diag(life_ex[r])), axis=1))

        scenario_150_no_outbreak_total_deaths.append(regimes_150_no_outbreak_total_deaths)
        scenario_300_no_outbreak_total_deaths.append(regimes_300_no_outbreak_total_deaths)

        scenario_150_no_outbreak_total_years_of_life_lost.append(regimes_150_no_outbreak_total_years_of_life_lost)
        scenario_300_no_outbreak_total_years_of_life_lost.append(regimes_300_no_outbreak_total_years_of_life_lost)
    
    _150_no_outbreak_total_deaths.append(scenario_150_no_outbreak_total_deaths)
    _300_no_outbreak_total_deaths.append(scenario_300_no_outbreak_total_deaths)

    _150_no_outbreak_total_years_of_life_lost.append(scenario_150_no_outbreak_total_years_of_life_lost)
    _300_no_outbreak_total_years_of_life_lost.append(scenario_300_no_outbreak_total_years_of_life_lost)

_150_no_outbreak_total_deaths = np.array(_150_no_outbreak_total_deaths)
_300_no_outbreak_total_deaths = np.array(_300_no_outbreak_total_deaths)

_150_no_outbreak_total_years_of_life_lost = np.array(_150_no_outbreak_total_years_of_life_lost)
_300_no_outbreak_total_years_of_life_lost = np.array(_300_no_outbreak_total_years_of_life_lost)

In [26]:
# Simulate for all the regions (sum over all age groups)
waned_0_no_outbreak_outputs_percent = []
immune_0_no_outbreak_outputs_percent = []
rec_0_no_outbreak_outputs_percent = []
susc_0_no_outbreak_outputs_percent = []

waned_150_no_outbreak_outputs_percent = []
immune_150_no_outbreak_outputs_percent = []
rec_150_no_outbreak_outputs_percent = []
susc_150_no_outbreak_outputs_percent = []

waned_300_no_outbreak_outputs_percent = []
immune_300_no_outbreak_outputs_percent = []
rec_300_no_outbreak_outputs_percent = []
susc_300_no_outbreak_outputs_percent = []

for s, scenario in enumerate(scenario_names):
    scenario_waned_0_no_outbreak_outputs_percent = []
    scenario_immune_0_no_outbreak_outputs_percent = []
    scenario_rec_0_no_outbreak_outputs_percent = []
    scenario_susc_0_no_outbreak_outputs_percent = []

    scenario_waned_150_no_outbreak_outputs_percent = []
    scenario_immune_150_no_outbreak_outputs_percent = []
    scenario_rec_150_no_outbreak_outputs_percent = []
    scenario_susc_150_no_outbreak_outputs_percent = []

    scenario_waned_300_no_outbreak_outputs_percent = []
    scenario_immune_300_no_outbreak_outputs_percent = []
    scenario_rec_300_no_outbreak_outputs_percent = []
    scenario_susc_300_no_outbreak_outputs_percent = []

    for R, regime in enumerate(regimes):
        regimes_waned_0_no_outbreak_outputs_percent = []
        regimes_immune_0_no_outbreak_outputs_percent = []
        regimes_rec_0_no_outbreak_outputs_percent = []
        regimes_susc_0_no_outbreak_outputs_percent = []

        regimes_waned_150_no_outbreak_outputs_percent = []
        regimes_immune_150_no_outbreak_outputs_percent = []
        regimes_rec_150_no_outbreak_outputs_percent = []
        regimes_susc_150_no_outbreak_outputs_percent = []

        regimes_waned_300_no_outbreak_outputs_percent = []
        regimes_immune_300_no_outbreak_outputs_percent = []
        regimes_rec_300_no_outbreak_outputs_percent = []
        regimes_susc_300_no_outbreak_outputs_percent = []

        for r, reg in enumerate(regions):
            # Partial and fully waned
            regimes_waned_0_no_outbreak_outputs_percent.append(((10**5) / np.sum(np.array(_150_no_outbreak_total_pop)[s, R, r, :])) * (
                _150_no_outbreak_outputs[s, R, r, 0, (3*len(age_groups)) : (4*len(age_groups))] +
                _150_no_outbreak_outputs[s, R, r, 0, (4*len(age_groups)) : (5*len(age_groups))] +
                _150_no_outbreak_outputs[s, R, r, 0, (5*len(age_groups)) : (6*len(age_groups))])
            )

            regimes_waned_150_no_outbreak_outputs_percent.append(((10**5) / np.sum(np.array(_150_no_outbreak_total_pop)[s, R, r, :])) * (
                _150_no_outbreak_outputs[s, R, r, -1, (3*len(age_groups)) : (4*len(age_groups))] +
                _150_no_outbreak_outputs[s, R, r, -1, (4*len(age_groups)) : (5*len(age_groups))] +
                _150_no_outbreak_outputs[s, R, r, -1, (5*len(age_groups)) : (6*len(age_groups))])
            )

            regimes_waned_300_no_outbreak_outputs_percent.append(((10**5) / np.sum(np.array(_300_no_outbreak_total_pop)[s, R, r, :])) * (
                _300_no_outbreak_outputs[s, R, r, -1, (3*len(age_groups)) : (4*len(age_groups))] +
                _300_no_outbreak_outputs[s, R, r, -1, (4*len(age_groups)) : (5*len(age_groups))] +
                _300_no_outbreak_outputs[s, R, r, -1, (5*len(age_groups)) : (6*len(age_groups))])
            )

            # High immunuity (recently boosted + fully vaccinated)
            regimes_immune_0_no_outbreak_outputs_percent.append(((10**5) / np.sum(np.array(_150_no_outbreak_total_pop)[s, R, r, :])) * (
                _150_no_outbreak_outputs[s, R, r, 0, (1*len(age_groups)) : (2*len(age_groups))] +
                _150_no_outbreak_outputs[s, R, r, 0, (2*len(age_groups)) : (3*len(age_groups))] +
                _150_no_outbreak_outputs[s, R, r, 0, (48*len(age_groups)) : (49*len(age_groups))])
            )

            regimes_immune_150_no_outbreak_outputs_percent.append(((10**5) / np.sum(np.array(_150_no_outbreak_total_pop)[s, R, r, :])) * (
                _150_no_outbreak_outputs[s, R, r, -1, (1*len(age_groups)) : (2*len(age_groups))] +
                _150_no_outbreak_outputs[s, R, r, -1, (2*len(age_groups)) : (3*len(age_groups))])
            )

            regimes_immune_300_no_outbreak_outputs_percent.append(((10**5) / np.sum(np.array(_300_no_outbreak_total_pop)[s, R, r, :])) * (
                _300_no_outbreak_outputs[s, R, r, -1, (1*len(age_groups)) : (2*len(age_groups))] +
                _300_no_outbreak_outputs[s, R, r, -1, (2*len(age_groups)) : (3*len(age_groups))])
            )

            # Recovered
            regimes_rec_0_no_outbreak_outputs_percent.append(((10**5) / np.sum(np.array(_150_no_outbreak_total_pop)[s, R, r, :])) * (
                _150_no_outbreak_outputs[s, R, r, 0, (48*len(age_groups)) : (49*len(age_groups))])
            )

            regimes_rec_150_no_outbreak_outputs_percent.append(((10**5) / np.sum(np.array(_150_no_outbreak_total_pop)[s, R, r, :])) * (
                _150_no_outbreak_outputs[s, R, r, -1, (48*len(age_groups)) : (49*len(age_groups))])
            )

            regimes_rec_300_no_outbreak_outputs_percent.append(((10**5) / np.sum(np.array(_300_no_outbreak_total_pop)[s, R, r, :])) * (
                _300_no_outbreak_outputs[s, R, r, -1, (48*len(age_groups)) : (49*len(age_groups))])
            )

            # Fully susceptible + Exposed + Infected
            regimes_susc_0_no_outbreak_outputs_percent.append(((10**5) / np.sum(np.array(_150_no_outbreak_total_pop)[s, R, r, :])) * (
                np.array(_150_no_outbreak_total_pop)[s, R, r, :] -
                _150_no_outbreak_outputs[s, R, r, 0, (3*len(age_groups)) : (4*len(age_groups))] -
                _150_no_outbreak_outputs[s, R, r, 0, (4*len(age_groups)) : (5*len(age_groups))] -
                _150_no_outbreak_outputs[s, R, r, 0, (5*len(age_groups)) : (6*len(age_groups))] -
                _150_no_outbreak_outputs[s, R, r, 0, (1*len(age_groups)) : (2*len(age_groups))] -
                _150_no_outbreak_outputs[s, R, r, 0, (2*len(age_groups)) : (3*len(age_groups))] -
                _150_no_outbreak_outputs[s, R, r, 0, (48*len(age_groups)) : (49*len(age_groups))])
            )

            regimes_susc_150_no_outbreak_outputs_percent.append(((10**5) / np.sum(np.array(_150_no_outbreak_total_pop)[s, R, r, :])) * (
                np.array(_150_no_outbreak_total_pop)[s, R, r, :] -
                _150_no_outbreak_outputs[s, R, r, -1, (3*len(age_groups)) : (4*len(age_groups))] -
                _150_no_outbreak_outputs[s, R, r, -1, (4*len(age_groups)) : (5*len(age_groups))] -
                _150_no_outbreak_outputs[s, R, r, -1, (5*len(age_groups)) : (6*len(age_groups))] -
                _150_no_outbreak_outputs[s, R, r, -1, (1*len(age_groups)) : (2*len(age_groups))] -
                _150_no_outbreak_outputs[s, R, r, -1, (2*len(age_groups)) : (3*len(age_groups))] -
                _150_no_outbreak_outputs[s, R, r, -1, (48*len(age_groups)) : (49*len(age_groups))])
            )

            regimes_susc_300_no_outbreak_outputs_percent.append(((10**5) / np.sum(np.array(_300_no_outbreak_total_pop)[s, R, r, :])) * (
                np.array(_300_no_outbreak_total_pop)[s, R, r, :] -
                _300_no_outbreak_outputs[s, R, r, -1, (3*len(age_groups)) : (4*len(age_groups))] -
                _300_no_outbreak_outputs[s, R, r, -1, (4*len(age_groups)) : (5*len(age_groups))] -
                _300_no_outbreak_outputs[s, R, r, -1, (5*len(age_groups)) : (6*len(age_groups))] -
                _300_no_outbreak_outputs[s, R, r, -1, (1*len(age_groups)) : (2*len(age_groups))] -
                _300_no_outbreak_outputs[s, R, r, -1, (2*len(age_groups)) : (3*len(age_groups))] -
                _300_no_outbreak_outputs[s, R, r, -1, (48*len(age_groups)) : (49*len(age_groups))])
            )
            
        scenario_waned_0_no_outbreak_outputs_percent.append(regimes_waned_0_no_outbreak_outputs_percent)
        scenario_immune_0_no_outbreak_outputs_percent.append(regimes_immune_0_no_outbreak_outputs_percent)
        scenario_rec_0_no_outbreak_outputs_percent.append(regimes_rec_0_no_outbreak_outputs_percent)
        scenario_susc_0_no_outbreak_outputs_percent.append(regimes_susc_0_no_outbreak_outputs_percent)

        scenario_waned_150_no_outbreak_outputs_percent.append(regimes_waned_150_no_outbreak_outputs_percent)
        scenario_immune_150_no_outbreak_outputs_percent.append(regimes_immune_150_no_outbreak_outputs_percent)
        scenario_rec_150_no_outbreak_outputs_percent.append(regimes_rec_150_no_outbreak_outputs_percent)
        scenario_susc_150_no_outbreak_outputs_percent.append(regimes_susc_150_no_outbreak_outputs_percent)
        
        scenario_waned_300_no_outbreak_outputs_percent.append(regimes_waned_300_no_outbreak_outputs_percent)
        scenario_immune_300_no_outbreak_outputs_percent.append(regimes_immune_300_no_outbreak_outputs_percent)
        scenario_rec_300_no_outbreak_outputs_percent.append(regimes_rec_300_no_outbreak_outputs_percent)
        scenario_susc_300_no_outbreak_outputs_percent.append(regimes_susc_300_no_outbreak_outputs_percent)
    
    waned_0_no_outbreak_outputs_percent.append(scenario_waned_0_no_outbreak_outputs_percent)
    immune_0_no_outbreak_outputs_percent.append(scenario_immune_0_no_outbreak_outputs_percent)
    rec_0_no_outbreak_outputs_percent.append(scenario_rec_0_no_outbreak_outputs_percent)
    susc_0_no_outbreak_outputs_percent.append(scenario_susc_0_no_outbreak_outputs_percent)

    waned_150_no_outbreak_outputs_percent.append(scenario_waned_150_no_outbreak_outputs_percent)
    immune_150_no_outbreak_outputs_percent.append(scenario_immune_150_no_outbreak_outputs_percent)
    rec_150_no_outbreak_outputs_percent.append(scenario_rec_150_no_outbreak_outputs_percent)
    susc_150_no_outbreak_outputs_percent.append(scenario_susc_150_no_outbreak_outputs_percent)

    waned_300_no_outbreak_outputs_percent.append(scenario_waned_300_no_outbreak_outputs_percent)
    immune_300_no_outbreak_outputs_percent.append(scenario_immune_300_no_outbreak_outputs_percent)
    rec_300_no_outbreak_outputs_percent.append(scenario_rec_300_no_outbreak_outputs_percent)
    susc_300_no_outbreak_outputs_percent.append(scenario_susc_300_no_outbreak_outputs_percent)

waned_0_no_outbreak_outputs_percent = np.array(waned_0_no_outbreak_outputs_percent)
immune_0_no_outbreak_outputs_percent = np.array(immune_0_no_outbreak_outputs_percent)
rec_0_no_outbreak_outputs_percent = np.array(rec_0_no_outbreak_outputs_percent)
susc_0_no_outbreak_outputs_percent = np.array(susc_0_no_outbreak_outputs_percent)

waned_150_no_outbreak_outputs_percent = np.array(waned_150_no_outbreak_outputs_percent)
immune_150_no_outbreak_outputs_percent = np.array(immune_150_no_outbreak_outputs_percent)
rec_150_no_outbreak_outputs_percent = np.array(rec_150_no_outbreak_outputs_percent)
susc_150_no_outbreak_outputs_percent = np.array(susc_150_no_outbreak_outputs_percent)

waned_300_no_outbreak_outputs_percent = np.array(waned_300_no_outbreak_outputs_percent)
immune_300_no_outbreak_outputs_percent = np.array(immune_300_no_outbreak_outputs_percent)
rec_300_no_outbreak_outputs_percent = np.array(rec_300_no_outbreak_outputs_percent)
susc_300_no_outbreak_outputs_percent = np.array(susc_300_no_outbreak_outputs_percent)

In [27]:
# Set up traces to plot _300_no_outbreak
total_years_of_life_lost_mean = []
total_years_of_life_lost_upper = []
total_years_of_life_lost_lower = []

_150_no_outbreak_total_deaths_mean = []
_150_no_outbreak_total_deaths_upper = []
_150_no_outbreak_total_deaths_lower = []

_300_no_outbreak_total_deaths_mean = []
_300_no_outbreak_total_deaths_upper = []
_300_no_outbreak_total_deaths_lower = []

_150_no_outbreak_total_years_of_life_lost_mean = []
_150_no_outbreak_total_years_of_life_lost_upper = []
_150_no_outbreak_total_years_of_life_lost_lower = []

_300_no_outbreak_total_years_of_life_lost_mean = []
_300_no_outbreak_total_years_of_life_lost_upper = []
_300_no_outbreak_total_years_of_life_lost_lower = []

total_reduction_to_s1_cum_years_of_life_lost_mean = []
total_reduction_to_s1_cum_years_of_life_lost_upper = []
total_reduction_to_s1_cum_years_of_life_lost_lower = []

total_reduction_to_s7_cum_years_of_life_lost_mean = []
total_reduction_to_s7_cum_years_of_life_lost_upper = []
total_reduction_to_s7_cum_years_of_life_lost_lower = []

total_cum_years_of_life_lost_mean = []
total_cum_years_of_life_lost_upper = []
total_cum_years_of_life_lost_lower = []

waned_0_no_outbreak_outputs_percent_mean = []
immune_0_no_outbreak_outputs_percent_mean = []
rec_0_no_outbreak_outputs_percent_mean = []
susc_0_no_outbreak_outputs_percent_mean = []

waned_150_no_outbreak_outputs_percent_mean = []
immune_150_no_outbreak_outputs_percent_mean = []
rec_150_no_outbreak_outputs_percent_mean = []
susc_150_no_outbreak_outputs_percent_mean = []

waned_300_no_outbreak_outputs_percent_mean = []
immune_300_no_outbreak_outputs_percent_mean = []
rec_300_no_outbreak_outputs_percent_mean = []
susc_300_no_outbreak_outputs_percent_mean = []

for r, _ in enumerate(regions):
    # Compute the mean 
    waned_0_no_outbreak_outputs_percent_mean.append(np.mean(waned_0_no_outbreak_outputs_percent[:,:,r,:], axis=1))
    immune_0_no_outbreak_outputs_percent_mean.append(np.mean(immune_0_no_outbreak_outputs_percent[:,:,r,:], axis=1))
    rec_0_no_outbreak_outputs_percent_mean.append(np.mean(rec_0_no_outbreak_outputs_percent[:,:,r,:], axis=1))
    susc_0_no_outbreak_outputs_percent_mean.append(np.mean(susc_0_no_outbreak_outputs_percent[:,:,r,:], axis=1))
    
    waned_150_no_outbreak_outputs_percent_mean.append(np.mean(waned_150_no_outbreak_outputs_percent[:,:,r,:], axis=1))
    immune_150_no_outbreak_outputs_percent_mean.append(np.mean(immune_150_no_outbreak_outputs_percent[:,:,r,:], axis=1))
    rec_150_no_outbreak_outputs_percent_mean.append(np.mean(rec_150_no_outbreak_outputs_percent[:,:,r,:], axis=1))
    susc_150_no_outbreak_outputs_percent_mean.append(np.mean(susc_150_no_outbreak_outputs_percent[:,:,r,:], axis=1))
    
    waned_300_no_outbreak_outputs_percent_mean.append(np.mean(waned_300_no_outbreak_outputs_percent[:,:,r,:], axis=1))
    immune_300_no_outbreak_outputs_percent_mean.append(np.mean(immune_300_no_outbreak_outputs_percent[:,:,r,:], axis=1))
    rec_300_no_outbreak_outputs_percent_mean.append(np.mean(rec_300_no_outbreak_outputs_percent[:,:,r,:], axis=1))
    susc_300_no_outbreak_outputs_percent_mean.append(np.mean(susc_300_no_outbreak_outputs_percent[:,:,r,:], axis=1))
    
    total_years_of_life_lost_mean.append(np.mean(total_years_of_life_lost[:,:,r,:], axis=1))
    _150_no_outbreak_total_deaths_mean.append(np.mean(_150_no_outbreak_total_deaths[:,:,r,:], axis=1))
    _300_no_outbreak_total_deaths_mean.append(np.mean(_300_no_outbreak_total_deaths[:,:,r,:], axis=1))
    _150_no_outbreak_total_years_of_life_lost_mean.append(np.mean(_150_no_outbreak_total_years_of_life_lost[:,:,r,:], axis=1))
    _300_no_outbreak_total_years_of_life_lost_mean.append(np.mean(_300_no_outbreak_total_years_of_life_lost[:,:,r,:], axis=1))
    total_reduction_to_s1_cum_years_of_life_lost_mean.append(np.mean(total_reduction_to_s1_cum_years_of_life_lost[:,:,r], axis=1))
    total_reduction_to_s7_cum_years_of_life_lost_mean.append(np.mean(total_reduction_to_s7_cum_years_of_life_lost[:,:,r], axis=1))
    total_cum_years_of_life_lost_mean.append(np.mean(total_cum_years_of_life_lost[:,:,r,:], axis=1))

    # Compute the upper quantiles
    total_years_of_life_lost_upper.append(np.quantile(total_years_of_life_lost[:,:,r,:], 0.975, axis=1))
    _150_no_outbreak_total_deaths_upper.append(np.quantile(_150_no_outbreak_total_deaths[:,:,r,:], 0.975, axis=1))
    _300_no_outbreak_total_deaths_upper.append(np.quantile(_300_no_outbreak_total_deaths[:,:,r,:], 0.975, axis=1))
    _150_no_outbreak_total_years_of_life_lost_upper.append(np.quantile(_150_no_outbreak_total_years_of_life_lost[:,:,r,:], 0.975, axis=1))
    _300_no_outbreak_total_years_of_life_lost_upper.append(np.quantile(_300_no_outbreak_total_years_of_life_lost[:,:,r,:], 0.975, axis=1))
    total_reduction_to_s1_cum_years_of_life_lost_upper.append(np.quantile(total_reduction_to_s1_cum_years_of_life_lost[:,:,r], 0.975, axis=1))
    total_reduction_to_s7_cum_years_of_life_lost_upper.append(np.quantile(total_reduction_to_s7_cum_years_of_life_lost[:,:,r], 0.975, axis=1))
    total_cum_years_of_life_lost_upper.append(np.quantile(total_cum_years_of_life_lost[:,:,r,:], 0.975, axis=1))

    # Compute the lower qunatiles
    total_years_of_life_lost_lower.append(np.quantile(total_years_of_life_lost[:,:,r,:], 0.025, axis=1))
    _150_no_outbreak_total_deaths_lower.append(np.quantile(_150_no_outbreak_total_deaths[:,:,r,:], 0.025, axis=1))
    _300_no_outbreak_total_deaths_lower.append(np.quantile(_300_no_outbreak_total_deaths[:,:,r,:], 0.025, axis=1))
    _150_no_outbreak_total_years_of_life_lost_lower.append(np.quantile(_150_no_outbreak_total_years_of_life_lost[:,:,r,:], 0.025, axis=1))
    _300_no_outbreak_total_years_of_life_lost_lower.append(np.quantile(_300_no_outbreak_total_years_of_life_lost[:,:,r,:], 0.025, axis=1))
    total_reduction_to_s1_cum_years_of_life_lost_lower.append(np.quantile(total_reduction_to_s1_cum_years_of_life_lost[:,:,r], 0.025, axis=1))
    total_reduction_to_s7_cum_years_of_life_lost_lower.append(np.quantile(total_reduction_to_s7_cum_years_of_life_lost[:,:,r], 0.025, axis=1))
    total_cum_years_of_life_lost_lower.append(np.quantile(total_cum_years_of_life_lost[:,:,r,:], 0.025, axis=1))

### Plot the time series of numbers of years of life lost for the different regions

In [28]:
# Trace names - represent the solver used for the simulation
trace_name = ['Scenario {}'.format(s+1) for s, scenario in enumerate(scenario_names[:-1])] + [scenario_names[-1]]

best_scenario_num = [[1], [1], [1], [1, 2], [1, 2, 3, 4], [1, 2], [1, 2, 3, 4], [1, 2]]

# Plot for each region
for r, reg in enumerate(regions):
    fig = go.Figure()
    # Plot for each boosting scenario
    for s, scenario in enumerate(scenario_names):
        fig.add_trace(
            go.Scatter(
                y=total_cum_years_of_life_lost_mean[r][s, :],
                x=times,
                mode='lines',
                name=trace_name[s],
                line=dict(
                    color=colours[s])
            )
        )

    for s in best_scenario_num[r]:
        fig.data[s-1].name = '(BEST) ' + trace_name[s-1]

    # Plot for each boosting scenario
    for s, scenario in enumerate(scenario_names):
        fig.add_trace(
            go.Scatter(
                y=total_cum_years_of_life_lost_upper[r][s, :].tolist() + total_cum_years_of_life_lost_lower[r][s, :].tolist()[::-1],
                x=times + times[::-1],
                mode='lines',
                name=trace_name[s],
                fill='toself',
                fillcolor=colours[s],
                line_color=colours[s],
                opacity=0.15,
                showlegend=False
            )
        )

    # Add axis labels
    fig.update_layout(
        boxmode='group',
        title='{}'.format(reg),
        width=800,
        height=500,
        plot_bgcolor='white',
        xaxis=dict(
            linecolor='black',
            title='Time (days)'),
        yaxis=dict(
            linecolor='black',
            title='Years of Life Lost (per 100k)',
            range=[0, 80]),
        hovermode='x unified'
        )

    fig.write_image('images/report2_economic/Years of Life Lost for {}.pdf'.format(reg))
    fig.show()

### Plot the time series of numbers of years lost for different scenarios

In [29]:
# Trace names - represent the solver used for the simulation
trace_name = ['{}'.format(r) for r in regions]

names = ['Scenario {}'.format(s+1) for s, scenario in enumerate(scenario_names[:-1])] + [scenario_names[-1]]

# Plot for each boosting scenario
for s, scenario in enumerate(scenario_names):
    fig = go.Figure()
    # Plot (line plot for each solver method for each age)
    for r, reg in enumerate(regions):
        if r % 2 == 1:
            fig.add_trace(
                go.Scatter(
                    y=total_cum_years_of_life_lost_mean[r][s, :],
                    x=times,
                    mode='lines',
                    name=trace_name[r],
                    line=dict(
                        color=colours[int(np.floor(r / 2))],
                        dash='dash')
                )
            )
        else:
            fig.add_trace(
                go.Scatter(
                    y=total_cum_years_of_life_lost_mean[r][s, :],
                    x=times,
                    mode='lines',
                    name=trace_name[r],
                    line=dict(
                        color=colours[int(np.floor(r / 2))])
                )
            )

        fig.add_trace(
            go.Scatter(
                y=total_cum_years_of_life_lost_upper[r][s, :].tolist() + total_cum_years_of_life_lost_lower[r][s, :].tolist()[::-1],
                x=times + times[::-1],
                mode='lines',
                name=trace_name[r],
                fill='toself',
                fillcolor=colours[int(np.floor(r / 2))],
                line_color=colours[int(np.floor(r / 2))],
                opacity=0.15,
                showlegend=False
            )
        )

    # Add axis labels
    fig.update_layout(
        boxmode='group',
        title='{}'.format(names[s]),
        width=800,
        height=500,
        plot_bgcolor='white',
        xaxis=dict(
            linecolor='black',
            title='Time (days)'),
        yaxis=dict(
            linecolor='black',
            title='Years of Life Lost (per 100k)',
            range=[0, 80]),
        hovermode='x unified'
        )

    fig.write_image('images/report2_economic/Years of Life Lost Scenario {}.pdf'.format(s+1))
    fig.show()

### Cumulative reductions compared to scenarios 

In [30]:
# Trace names - represent the solver used for the simulation
trace_name = [
    ['Scenario 1', 'Scenario 2 & 3', 'Scenario 2 & 3', 'Scenario 4', 'Scenario 5 & 6', 'Scenario 5 & 6'] + [scenario_names[-1]],
    ['Scenario 1', 'Scenario 2 & 3', 'Scenario 2 & 3', 'Scenario 4', 'Scenario 5 & 6', 'Scenario 5 & 6'] + [scenario_names[-1]],
    ['Scenario 1', 'Scenario 2', 'Scenario 3', 'Scenario 4', 'Scenario 5 & 6', 'Scenario 5 & 6'] + [scenario_names[-1]],
    ['Scenario 1 & 2', 'Scenario 1 & 2', 'Scenario 3', 'Scenario 4', 'Scenario 5 & 6', 'Scenario 5 & 6'] + [scenario_names[-1]],
    ['Scenario 1, 2, 3 & 4', 'Scenario 1, 2, 3 & 4', 'Scenario 1, 2, 3 & 4', 'Scenario 1, 2, 3 & 4', 'Scenario 5 & 6', 'Scenario 5 & 6'] + [scenario_names[-1]],
    ['Scenario 1 & 2', 'Scenario 1 & 2', 'Scenario 3', 'Scenario 4', 'Scenario 5 & 6', 'Scenario 5 & 6'] + [scenario_names[-1]],
    ['Scenario 1, 2, 3 & 4', 'Scenario 1, 2, 3 & 4', 'Scenario 1, 2, 3 & 4', 'Scenario 1, 2, 3 & 4', 'Scenario 5 & 6', 'Scenario 5 & 6'] + [scenario_names[-1]],
    ['Scenario 1 & 2', 'Scenario 1 & 2', 'Scenario 3', 'Scenario 4', 'Scenario 5 & 6', 'Scenario 5 & 6'] + [scenario_names[-1]]
]

dash_name = [
    ['solid', 'solid', 'solid', 'longdashdot', 'dash', 'dash', 'dot'],
    ['solid', 'solid', 'solid', 'longdashdot', 'dash', 'dash', 'dot'],
    ['solid', 'solid', 'dashdot', 'longdashdot', 'dash', 'dash', 'dot'],
    ['solid', 'solid', 'dashdot', 'longdashdot', 'dash', 'dash', 'dot'],
    ['solid', 'solid', 'solid', 'solid', 'dash', 'dash', 'dot'],
    ['solid', 'solid', 'dashdot', 'longdashdot', 'dash', 'dash', 'dot'],
    ['solid', 'solid', 'solid', 'solid', 'dash', 'dash', 'dot'],
    ['solid', 'solid', 'dashdot', 'longdashdot', 'dash', 'dash', 'dot']
]

inlegend = [
    [True, False, True, True, False, True, True],
    [True, False, True, True, False, True, True],
    [True, True, True, True, False, True, True],
    [False, True, True, True, False, True, True],
    [False, False, False, True, False, True, True],
    [False, True, True, True, False, True, True],
    [False, False, False, True, False, True, True],
    [False, True, True, True, False, True, True]
]

# Plot for each region
for r, reg in enumerate(regions):
    fig = go.Figure()
    # Plot for each boosting scenario
    for s, scenario in enumerate(scenario_names[1:]):
        if inlegend[r][s+1] == True:
            fig.add_trace(
                go.Scatter(
                    y=total_reduction_to_s1_cum_years_of_life_lost_mean[r][s+1, :],
                    x=times,
                    mode='lines',
                    name=trace_name[r][s+1],
                    line=dict(
                        color=cb_colours[s+1],
                        dash=dash_name[r][s+1]),
                    showlegend=inlegend[r][s+1]
                )
            )

    # Plot for each boosting scenario
    for s, scenario in enumerate(scenario_names[1:]):
        if inlegend[r][s+1] == True:
            fig.add_trace(
                go.Scatter(
                    y=total_reduction_to_s1_cum_years_of_life_lost_upper[r][s+1, :].tolist() + total_reduction_to_s1_cum_years_of_life_lost_lower[r][s+1, :].tolist()[::-1],
                    x=times + times[::-1],
                    mode='lines',
                    name=trace_name[r][s+1],
                    fill='toself',
                    fillcolor=cb_colours[s+1],
                    line_color=cb_colours[s+1],
                    opacity=0.15,
                    showlegend=False
                )
            )

    # Add axis labels
    fig.update_layout(
        boxmode='group',
        title='{}'.format(reg),
        width=650,
        height=500,
        plot_bgcolor='white',
        font=dict(
            size=16),
        xaxis=dict(
            linecolor='black',
            title='Time (days)'),
        yaxis=dict(
            linecolor='black',
            title='Percentage increase<br>in cumulative Years of Life Lost',
            range=[0, 70]),
        hovermode='x unified',
        legend=dict(
            yanchor="bottom",
            y=0.75,
            xanchor="right",
            x=1,
            bordercolor="Black",
            borderwidth=1
        )
        )

    fig.write_image('images/report2_economic/CB Increase to S1 Years of Life Lost for {}.pdf'.format(reg))
    fig.show()

In [31]:
# Trace names - represent the solver used for the simulation
trace_name = [
    ['Scenario 1', 'Scenario 2 & 3', 'Scenario 2 & 3', 'Scenario 4', 'Scenario 5 & 6', 'Scenario 5 & 6'] + [scenario_names[-1]],
    ['Scenario 1', 'Scenario 2 & 3', 'Scenario 2 & 3', 'Scenario 4', 'Scenario 5 & 6', 'Scenario 5 & 6'] + [scenario_names[-1]],
    ['Scenario 1', 'Scenario 2', 'Scenario 3', 'Scenario 4', 'Scenario 5 & 6', 'Scenario 5 & 6'] + [scenario_names[-1]],
    ['Scenario 1 & 2', 'Scenario 1 & 2', 'Scenario 3', 'Scenario 4', 'Scenario 5 & 6', 'Scenario 5 & 6'] + [scenario_names[-1]],
    ['Scenario 1, 2, 3 & 4', 'Scenario 1, 2, 3 & 4', 'Scenario 1, 2, 3 & 4', 'Scenario 1, 2, 3 & 4', 'Scenario 5 & 6', 'Scenario 5 & 6'] + [scenario_names[-1]],
    ['Scenario 1 & 2', 'Scenario 1 & 2', 'Scenario 3', 'Scenario 4', 'Scenario 5 & 6', 'Scenario 5 & 6'] + [scenario_names[-1]],
    ['Scenario 1, 2, 3 & 4', 'Scenario 1, 2, 3 & 4', 'Scenario 1, 2, 3 & 4', 'Scenario 1, 2, 3 & 4', 'Scenario 5 & 6', 'Scenario 5 & 6'] + [scenario_names[-1]],
    ['Scenario 1 & 2', 'Scenario 1 & 2', 'Scenario 3', 'Scenario 4', 'Scenario 5 & 6', 'Scenario 5 & 6'] + [scenario_names[-1]]
]

inlegend = [
    [True, False, True, True, False, True, True],
    [True, False, True, True, False, True, True],
    [True, True, True, True, False, True, True],
    [False, True, True, True, False, True, True],
    [False, False, False, True, False, True, True],
    [False, True, True, True, False, True, True],
    [False, False, False, True, False, True, True],
    [False, True, True, True, False, True, True]
]

# Plot for each region
for r, reg in enumerate(regions):
    fig = go.Figure()
    # Plot for each boosting scenario
    for s, scenario in enumerate(scenario_names[1:]):
        fig.add_trace(
            go.Scatter(
                y=total_reduction_to_s1_cum_years_of_life_lost_mean[r][s+1, :],
                x=times,
                mode='lines',
                name=trace_name[r][s+1],
                line=dict(
                    color=colours[s+1]),
                showlegend=inlegend[r][s+1]
            )
        )

    # Plot for each boosting scenario
    for s, scenario in enumerate(scenario_names[1:]):
        fig.add_trace(
            go.Scatter(
                y=total_reduction_to_s1_cum_years_of_life_lost_upper[r][s+1, :].tolist() + total_reduction_to_s1_cum_years_of_life_lost_lower[r][s+1, :].tolist()[::-1],
                x=times + times[::-1],
                mode='lines',
                name=trace_name[r][s+1],
                fill='toself',
                fillcolor=colours[s+1],
                line_color=colours[s+1],
                opacity=0.15,
                showlegend=False
            )
        )

    # Add axis labels
    fig.update_layout(
        boxmode='group',
        title='{}'.format(reg),
        width=800,
        height=500,
        plot_bgcolor='white',
        xaxis=dict(
            linecolor='black',
            title='Time (days)'),
        yaxis=dict(
            linecolor='black',
            title='Percentage increase<br>in Cumulative Years of Life Lost',
            range=[0, 150]),
        hovermode='x unified'
        )

    fig.write_image('images/report2_economic/Increase to S1 Years of Life Lost for {}.pdf'.format(reg))
    fig.show()

In [32]:
# Trace names - represent the solver used for the simulation
trace_name = [
    ['Scenario 1', 'Scenario 2 & 3', 'Scenario 2 & 3', 'Scenario 4', 'Scenario 5 & 6', 'Scenario 5 & 6'] + [scenario_names[-1]],
    ['Scenario 1', 'Scenario 2 & 3', 'Scenario 2 & 3', 'Scenario 4', 'Scenario 5 & 6', 'Scenario 5 & 6'] + [scenario_names[-1]],
    ['Scenario 1', 'Scenario 2', 'Scenario 3', 'Scenario 4', 'Scenario 5 & 6', 'Scenario 5 & 6'] + [scenario_names[-1]],
    ['Scenario 1 & 2', 'Scenario 1 & 2', 'Scenario 3', 'Scenario 4', 'Scenario 5 & 6', 'Scenario 5 & 6'] + [scenario_names[-1]],
    ['Scenario 1, 2, 3 & 4', 'Scenario 1, 2, 3 & 4', 'Scenario 1, 2, 3 & 4', 'Scenario 1, 2, 3 & 4', 'Scenario 5 & 6', 'Scenario 5 & 6'] + [scenario_names[-1]],
    ['Scenario 1 & 2', 'Scenario 1 & 2', 'Scenario 3', 'Scenario 4', 'Scenario 5 & 6', 'Scenario 5 & 6'] + [scenario_names[-1]],
    ['Scenario 1, 2, 3 & 4', 'Scenario 1, 2, 3 & 4', 'Scenario 1, 2, 3 & 4', 'Scenario 1, 2, 3 & 4', 'Scenario 5 & 6', 'Scenario 5 & 6'] + [scenario_names[-1]],
    ['Scenario 1 & 2', 'Scenario 1 & 2', 'Scenario 3', 'Scenario 4', 'Scenario 5 & 6', 'Scenario 5 & 6'] + [scenario_names[-1]]
]

best_scenario_num = [[1], [1], [1], [1, 2], [1, 2, 3, 4], [1, 2], [1, 2, 3, 4], [1, 2]]
inlegend = [
    [True, False, True, True, False, True, True],
    [True, False, True, True, False, True, True],
    [True, True, True, True, False, True, True],
    [False, True, True, True, False, True, True],
    [False, False, False, True, False, True, True],
    [False, True, True, True, False, True, True],
    [False, False, False, True, False, True, True],
    [False, True, True, True, False, True, True]
]

# Plot for each region
for r, reg in enumerate(regions):
    fig = go.Figure()
    # Plot for each boosting scenario
    for s, scenario in enumerate(scenario_names[:-1]):
        fig.add_trace(
            go.Scatter(
                y=total_reduction_to_s7_cum_years_of_life_lost_mean[r][s, :],
                x=times,
                mode='lines',
                name=trace_name[r][s],
                line=dict(
                    color=colours[s]),
                showlegend=inlegend[r][s]
            )
        )

    for s in best_scenario_num[r]:
        fig.data[s-1].name = '(BEST) ' + trace_name[r][s-1]

    # Plot for each boosting scenario
    for s, scenario in enumerate(scenario_names[:-1]):
        fig.add_trace(
            go.Scatter(
                y=total_reduction_to_s7_cum_years_of_life_lost_upper[r][s, :].tolist() + total_reduction_to_s7_cum_years_of_life_lost_lower[r][s, :].tolist()[::-1],
                x=times + times[::-1],
                mode='lines',
                name=trace_name[r][s],
                fill='toself',
                fillcolor=colours[s],
                line_color=colours[s],
                opacity=0.15,
                showlegend=False
            )
        )

    # Add axis labels
    fig.update_layout(
        boxmode='group',
        title='{}'.format(reg),
        width=800,
        height=500,
        plot_bgcolor='white',
        xaxis=dict(
            linecolor='black',
            title='Time (days)'),
        yaxis=dict(
            linecolor='black',
            title='Percentage reduction<br>in Cumulative Years of Life Lost',
            range=[0, 60]),
        hovermode='x unified'
        )

    fig.write_image('images/report2_economic/Reduction to S7 Years of Life Lost for {}.pdf'.format(reg))
    fig.show()

## Summary Figure

### Cummulative Years of Life Lost

In [33]:
new_regions = ['UK'] + regions[1:]
trace_name = ['Scenario {}'.format(s+1) for s, scenario in enumerate(scenario_names[:-1])] + [scenario_names[-1]]

fig = go.Figure()
# Plot for each region
for s, scenario in enumerate(scenario_names):
    fig.add_trace(
        go.Bar(
            y=[np.sum(total_years_of_life_lost_mean[r][s, :]) for r, reg in enumerate(regions)],
            x=new_regions,
            name=trace_name[s],
            marker_color=cb_colours[s],
        )
    )

# Add axis labels
fig.update_layout(
    boxmode='group',
    title='Mean years of Life Lost per 100,000 for different countries and scenarios from {} simulations'.format(len(regimes)),
    width=1150,
    height=575,
    plot_bgcolor='white',
    font=dict(
            size=16),
    xaxis=dict(linecolor='black'),
    yaxis=dict(
        linecolor='black',
        title='Years of Life Lost  (per 100k)'),
    hovermode='x unified',
    legend=dict(
            orientation="h",
            yanchor="bottom",
            y=0.88,
            xanchor="right",
            x=1.0000001,
            bordercolor="Black",
            borderwidth=1
        )
    )

fig.write_image('images/report2_economic/CB Years of Life Lost per Scenario and Country.pdf')
fig.show()

In [34]:
new_colours = ['blue', 'orange', 'green', 'red', 'purple', 'deepskyblue', 'black']

trace_name = ['Scenario {}'.format(s+1) for s, scenario in enumerate(scenario_names[:-1])] + [scenario_names[-1]]

fig = go.Figure()
# Plot for each region
for s, scenario in enumerate(scenario_names):
    fig.add_trace(
        go.Bar(
            y=[np.sum(total_years_of_life_lost_mean[r][s, :]) for r, reg in enumerate(regions)],
            x=regions,
            name=trace_name[s],
            marker_color=new_colours[s],
        )
    )

# Add axis labels
fig.update_layout(
    boxmode='group',
    title='Mean years of Life Lost per 100,000 for different countries and scenarios from {} simulations'.format(len(regimes)),
    width=1000,
    height=500,
    plot_bgcolor='white',
    xaxis=dict(linecolor='black'),
    yaxis=dict(
        linecolor='black',
        title='Years of Life Lost  (per 100k)'),
    hovermode='x unified',
    legend=dict(
            orientation="h",
            yanchor="bottom",
            y=0.98,
            xanchor="right",
            x=1
        )
    )

fig.write_image('images/report2_economic/Years of Life Lost per Scenario and Country.pdf')
fig.show()

## Comparative reduction / increase in Years of Life Lost with CI

In [35]:
# Sort results
new_regions = ['UK'] + regions[1:]
trace_name = ['Scenario {}'.format(s+1) for s, scenario in enumerate(scenario_names[:-1])] + [scenario_names[-1]]

# Plot (box plot for inference)
fig = go.Figure()

for s, scenario in enumerate(scenario_names[1:]):
    fig.add_trace(
        go.Scatter(
            y=[total_reduction_to_s1_cum_years_of_life_lost_mean[r][s+1, -1] for r, reg in enumerate(regions)],
            x=np.arange(len(regions)) + s*0.12,
            mode='markers',
            error_y=dict(
                type='data',
                symmetric=False,
                color=cb_colours[s+1],
                array=[total_reduction_to_s1_cum_years_of_life_lost_upper[r][s+1, -1] - total_reduction_to_s1_cum_years_of_life_lost_mean[r][s+1, -1] for r, reg in enumerate(regions)],
                arrayminus=[total_reduction_to_s1_cum_years_of_life_lost_mean[r][s+1, -1] - total_reduction_to_s1_cum_years_of_life_lost_lower[r][s+1, -1] for r, reg in enumerate(regions)]
            ),
            name=trace_name[s+1],
            marker_color=cb_colours[s+1]
        )
    )

fig.add_hline(y=0, line_dash='dot', annotation_text='Baseline', fillcolor='black', annotation_position='bottom right')

fig.update_layout(
    boxmode='group',
    width=1000,
    height=500,
    plot_bgcolor='white',
    font=dict(
            size=16),
    xaxis=dict(
        linecolor='black',
        ticktext=new_regions,
        tickvals=np.arange(len(new_regions))+0.3
        ),
    yaxis=dict(
        linecolor='black',
        title='Percentage increase<br>in total Years of Life Lost'),
    hovermode='x unified',
    legend=dict(
            orientation="h",
            yanchor="bottom",
            y=0.98,
            xanchor="right",
            x=1
        )
    )

fig.write_image('images/report2_economic/CB Increase to S1 Years of Life Lost per Scenario and Country CI.pdf')
fig.show()

In [36]:
# Sort results
new_colours = ['blue', 'orange', 'green', 'red', 'purple', 'deepskyblue', 'black']

trace_name = ['Scenario {}'.format(s+1) for s, scenario in enumerate(scenario_names[:-1])] + [scenario_names[-1]]

# Plot (box plot for inference)
fig = go.Figure()

for s, scenario in enumerate(scenario_names[1:]):
    fig.add_trace(
        go.Scatter(
            y=[total_reduction_to_s1_cum_years_of_life_lost_mean[r][s+1, -1] for r, reg in enumerate(regions)],
            x=np.arange(len(regions)) + s*0.12,
            mode='markers',
            error_y=dict(
                type='data',
                symmetric=False,
                color=new_colours[s+1],
                array=[total_reduction_to_s1_cum_years_of_life_lost_upper[r][s+1, -1] - total_reduction_to_s1_cum_years_of_life_lost_mean[r][s+1, -1] for r, reg in enumerate(regions)],
                arrayminus=[total_reduction_to_s1_cum_years_of_life_lost_mean[r][s+1, -1] - total_reduction_to_s1_cum_years_of_life_lost_lower[r][s+1, -1] for r, reg in enumerate(regions)]
            ),
            name=trace_name[s+1],
            marker_color=new_colours[s+1]
        )
    )

fig.add_hline(y=0, line_dash='dot', annotation_text='Baseline', fillcolor='black', annotation_position='bottom right')

fig.update_layout(
    boxmode='group',
    width=1000,
    height=500,
    plot_bgcolor='white',
    xaxis=dict(
        linecolor='black',
        ticktext=regions,
        tickvals=np.arange(len(regions))+0.3
        ),
    yaxis=dict(
        linecolor='black',
        title='Percentage increase in Total Years of Life Lost'),
    hovermode='x unified',
    legend=dict(
            orientation="h",
            yanchor="bottom",
            y=0.98,
            xanchor="right",
            x=1
        )
    )

fig.write_image('images/report2_economic/Increase to S1 Years of Life Lost per Scenario and Country CI.pdf')
fig.show()

In [37]:
# Sort results
new_colours = ['blue', 'orange', 'green', 'red', 'purple', 'deepskyblue', 'black']

trace_name = ['Scenario {}'.format(s+1) for s, scenario in enumerate(scenario_names[:-1])] + [scenario_names[-1]]

# Plot (box plot for inference)
fig = go.Figure()

for s, scenario in enumerate(scenario_names[:-1]):
    fig.add_trace(
        go.Scatter(
            y=[total_reduction_to_s7_cum_years_of_life_lost_mean[r][s, -1] for r, reg in enumerate(regions)],
            x=np.arange(len(regions)) + s*0.12,
            mode='markers',
            error_y=dict(
                type='data',
                symmetric=False,
                color=new_colours[s],
                array=[total_reduction_to_s7_cum_years_of_life_lost_upper[r][s, -1] - total_reduction_to_s7_cum_years_of_life_lost_mean[r][s, -1] for r, reg in enumerate(regions)],
                arrayminus=[total_reduction_to_s7_cum_years_of_life_lost_mean[r][s, -1] - total_reduction_to_s7_cum_years_of_life_lost_lower[r][s, -1] for r, reg in enumerate(regions)]
            ),
            name=trace_name[s],
            marker_color=new_colours[s]
        )
    )

fig.add_hline(y=0, line_dash='dot', annotation_text='Baseline', fillcolor='black', annotation_position='bottom right')

fig.update_layout(
    boxmode='group',
    width=1000,
    height=500,
    plot_bgcolor='white',
    xaxis=dict(
        linecolor='black',
        ticktext=regions,
        tickvals=np.arange(len(regions))+0.3
        ),
    yaxis=dict(
        linecolor='black',
        title='Percentage reduction in Total Years of Life Lost'),
    hovermode='x unified',
    legend=dict(
            orientation="h",
            yanchor="bottom",
            y=0.98,
            xanchor="right",
            x=1.2
        )
    )

fig.write_image('images/report2_economic/Reduction to S7 Years of Life Lost per Scenario and Country CI.pdf')
fig.show()

## Immunity levels per strategy per country
### After 150 days with outbreak

In [68]:
new_colours = ['blue', 'orange', 'green', 'red', 'purple', 'deepskyblue', 'black']

trace_name = ['<b>Strategy {}</b>'.format(s+1) for s, scenario in enumerate(scenario_names)]

# Plot for each region
for r, reg in enumerate(regions):
    fig = go.Figure()
    fig = make_subplots(
        rows=int(np.ceil((len(scenario_names)-1)/3)), cols=3,
        specs=[[{'type': 'polar'}]*3]*int(np.ceil((len(scenario_names)-1)/3)),
        subplot_titles=tuple(trace_name[:-1]))
    for s, scenario in enumerate(scenario_names[:-1]):
        # Partially and fully waned
        fig.add_trace(
            go.Barpolar(
                r=np.nan_to_num(np.sqrt(waned_0_no_outbreak_outputs_percent_mean[r][s, :])),
                marker_color=['black'] * len(age_groups),
                name=trace_name[s],
                opacity=0.6,
                showlegend=False,
                text=age_groups,
                hoverinfo='text',
            ),
            row= int(np.floor(s / 3)) + 1,
            col= s % 3 + 1)

        # Recovered
        fig.add_trace(
            go.Barpolar(
                r=np.sqrt(waned_0_no_outbreak_outputs_percent_mean[r][s, :] + rec_0_no_outbreak_outputs_percent_mean[r][s, :]) -
                    np.nan_to_num(np.sqrt(waned_0_no_outbreak_outputs_percent_mean[r][s, :])),
                marker_color=['black'] * len(age_groups),
                name=trace_name[s],
                opacity=0.8,
                showlegend=False,
                text=age_groups,
                hoverinfo='text'
            ),
            row= int(np.floor(s / 3)) + 1,
            col= s % 3 + 1)

        # Recently boosted + Fully vaccinated
        fig.add_trace(
            go.Barpolar(
                r=np.sqrt(waned_0_no_outbreak_outputs_percent_mean[r][s, :] + rec_0_no_outbreak_outputs_percent_mean[r][s, :] + immune_0_no_outbreak_outputs_percent_mean[r][s, :]) -
                    np.sqrt(waned_0_no_outbreak_outputs_percent_mean[r][s, :] + rec_0_no_outbreak_outputs_percent_mean[r][s, :]),
                marker_color=[new_colours[s]] * len(age_groups),
                name=trace_name[s],
                opacity=1,
                showlegend=False,
                text=age_groups,
                hoverinfo='text'
            ),
            row= int(np.floor(s / 3)) + 1,
            col= s % 3 + 1)

        # Fully susceptible + Exposed + Infected
        fig.add_trace(
            go.Barpolar(
                r=np.sqrt(waned_0_no_outbreak_outputs_percent_mean[r][s, :] + rec_0_no_outbreak_outputs_percent_mean[r][s, :] + immune_0_no_outbreak_outputs_percent_mean[r][s, :] + susc_0_no_outbreak_outputs_percent_mean[r][s, :]) - 
                    np.sqrt(waned_0_no_outbreak_outputs_percent_mean[r][s, :] + rec_0_no_outbreak_outputs_percent_mean[r][s, :] + immune_0_no_outbreak_outputs_percent_mean[r][s, :]),
                marker_color=['gray'] * len(age_groups),
                marker_line_color='black',
                marker_line_width=2,
                name=trace_name[s],
                opacity=0.2,
                showlegend=False,
                text=age_groups,
                hoverinfo='text'
            ),
            row= int(np.floor(s / 3)) + 1,
            col= s % 3 + 1)

    fig.update_traces(text=age_groups)
    fig.update_layout(
        plot_bgcolor='white',
        title='<b>Immunity levels for different scenarios: {}</b>'.format(reg),
        width=1400,
        height=1300,
        template=None,
        font=dict(size=15),
        polar = dict(
            radialaxis = dict(
                showline = False,
                gridcolor = 'white',
                showticklabels=False,
                ticks=''),
            angularaxis = dict(
                showline = False,
                gridcolor = 'white',
                tickvals=(360/len(age_groups) * np.array(range(len(age_groups)))).tolist(),
                ticktext=age_groups,
                ticks='inside')
        ),
        polar2 = dict(
            radialaxis = dict(
                showline = False,
                gridcolor = 'white',
                showticklabels=False,
                ticks=''),
            angularaxis = dict(
                showline = False,
                gridcolor = 'white',
                tickvals=(360/len(age_groups) * np.array(range(len(age_groups)))).tolist(),
                ticktext=age_groups,
                ticks='inside')
        ),
        polar3 = dict(
            radialaxis = dict(
                showline = False,
                gridcolor = 'white',
                showticklabels=False,
                ticks=''),
            angularaxis = dict(
                showline = False,
                gridcolor = 'white',
                tickvals=(360/len(age_groups) * np.array(range(len(age_groups)))).tolist(),
                ticktext=age_groups,
                ticks='inside')
        ),
        polar4 = dict(
            radialaxis = dict(
                showline = False,
                gridcolor = 'white',
                showticklabels=False,
                ticks=''),
            angularaxis = dict(
                showline = False,
                gridcolor = 'white',
                tickvals=(360/len(age_groups) * np.array(range(len(age_groups)))).tolist(),
                ticktext=age_groups,
                ticks='inside')
        ),
        polar5 = dict(
            radialaxis = dict(
                showline = False,
                gridcolor = 'white',
                showticklabels=False,
                ticks=''),
            angularaxis = dict(
                showline = False,
                gridcolor = 'white',
                tickvals=(360/len(age_groups) * np.array(range(len(age_groups)))).tolist(),
                ticktext=age_groups,
                ticks='inside')
        ),
        polar6 = dict(
            radialaxis = dict(
                showline = False,
                gridcolor = 'white',
                showticklabels=False,
                ticks=''),
            angularaxis = dict(
                showline = False,
                gridcolor = 'white',
                tickvals=(360/len(age_groups) * np.array(range(len(age_groups)))).tolist(),
                ticktext=age_groups,
                ticks='inside')
        ),
        bargap=0.05
    )

    fig.write_image('images/report2_economic/Initial No outbreak Immunity levels per Scenario {}.pdf'.format(reg))
    fig.show()


### After 150 days with no outbreak

In [69]:
new_colours = ['blue', 'orange', 'green', 'red', 'purple', 'deepskyblue', 'black']

trace_name = ['<b>Strategy {}</b>'.format(s+1) for s, scenario in enumerate(scenario_names)]

# Plot for each region
for r, reg in enumerate(regions):
    fig = go.Figure()
    fig = make_subplots(
        rows=int(np.ceil((len(scenario_names)-1)/3)), cols=3,
        specs=[[{'type': 'polar'}]*3]*int(np.ceil((len(scenario_names)-1)/3)),
        subplot_titles=tuple(trace_name[:-1]))
    for s, scenario in enumerate(scenario_names[:-1]):
        # Partially and fully waned
        fig.add_trace(
            go.Barpolar(
                r=np.nan_to_num(np.sqrt(waned_150_no_outbreak_outputs_percent_mean[r][s, :])),
                marker_color=['black'] * len(age_groups),
                name=trace_name[s],
                opacity=0.6,
                showlegend=False,
                text=age_groups,
                hoverinfo='text',
            ),
            row= int(np.floor(s / 3)) + 1,
            col= s % 3 + 1)

        # Recovered
        fig.add_trace(
            go.Barpolar(
                r=np.sqrt(waned_150_no_outbreak_outputs_percent_mean[r][s, :] + rec_150_no_outbreak_outputs_percent_mean[r][s, :]) -
                    np.nan_to_num(np.sqrt(waned_150_no_outbreak_outputs_percent_mean[r][s, :])),
                marker_color=['black'] * len(age_groups),
                name=trace_name[s],
                opacity=0.8,
                showlegend=False,
                text=age_groups,
                hoverinfo='text'
            ),
            row= int(np.floor(s / 3)) + 1,
            col= s % 3 + 1)

        # Recently boosted + Fully vaccinated
        fig.add_trace(
            go.Barpolar(
                r=np.sqrt(waned_150_no_outbreak_outputs_percent_mean[r][s, :] + rec_150_no_outbreak_outputs_percent_mean[r][s, :] + immune_150_no_outbreak_outputs_percent_mean[r][s, :]) -
                    np.sqrt(waned_150_no_outbreak_outputs_percent_mean[r][s, :] + rec_150_no_outbreak_outputs_percent_mean[r][s, :]),
                marker_color=[new_colours[s]] * len(age_groups),
                name=trace_name[s],
                opacity=1,
                showlegend=False,
                text=age_groups,
                hoverinfo='text'
            ),
            row= int(np.floor(s / 3)) + 1,
            col= s % 3 + 1)

        # Fully susceptible + Exposed + Infected
        fig.add_trace(
            go.Barpolar(
                r=np.sqrt(waned_150_no_outbreak_outputs_percent_mean[r][s, :] + rec_150_no_outbreak_outputs_percent_mean[r][s, :] + immune_150_no_outbreak_outputs_percent_mean[r][s, :] + susc_150_no_outbreak_outputs_percent_mean[r][s, :]) - 
                    np.sqrt(waned_150_no_outbreak_outputs_percent_mean[r][s, :] + rec_150_no_outbreak_outputs_percent_mean[r][s, :] + immune_150_no_outbreak_outputs_percent_mean[r][s, :]),
                marker_color=['gray'] * len(age_groups),
                marker_line_color='black',
                marker_line_width=2,
                name=trace_name[s],
                opacity=0.2,
                showlegend=False,
                text=age_groups,
                hoverinfo='text'
            ),
            row= int(np.floor(s / 3)) + 1,
            col= s % 3 + 1)

    fig.update_traces(text=age_groups)
    fig.update_layout(
        plot_bgcolor='white',
        title='<b>Immunity levels for different scenarios with no outbreak: {}</b>'.format(reg),
        width=1400,
        height=1300,
        template=None,
        font=dict(size=15),
        polar = dict(
            radialaxis = dict(
                showline = False,
                gridcolor = 'white',
                showticklabels=False,
                ticks=''),
            angularaxis = dict(
                showline = False,
                gridcolor = 'white',
                tickvals=(360/len(age_groups) * np.array(range(len(age_groups)))).tolist(),
                ticktext=age_groups,
                ticks='inside')
        ),
        polar2 = dict(
            radialaxis = dict(
                showline = False,
                gridcolor = 'white',
                showticklabels=False,
                ticks=''),
            angularaxis = dict(
                showline = False,
                gridcolor = 'white',
                tickvals=(360/len(age_groups) * np.array(range(len(age_groups)))).tolist(),
                ticktext=age_groups,
                ticks='inside')
        ),
        polar3 = dict(
            radialaxis = dict(
                showline = False,
                gridcolor = 'white',
                showticklabels=False,
                ticks=''),
            angularaxis = dict(
                showline = False,
                gridcolor = 'white',
                tickvals=(360/len(age_groups) * np.array(range(len(age_groups)))).tolist(),
                ticktext=age_groups,
                ticks='inside')
        ),
        polar4 = dict(
            radialaxis = dict(
                showline = False,
                gridcolor = 'white',
                showticklabels=False,
                ticks=''),
            angularaxis = dict(
                showline = False,
                gridcolor = 'white',
                tickvals=(360/len(age_groups) * np.array(range(len(age_groups)))).tolist(),
                ticktext=age_groups,
                ticks='inside')
        ),
        polar5 = dict(
            radialaxis = dict(
                showline = False,
                gridcolor = 'white',
                showticklabels=False,
                ticks=''),
            angularaxis = dict(
                showline = False,
                gridcolor = 'white',
                tickvals=(360/len(age_groups) * np.array(range(len(age_groups)))).tolist(),
                ticktext=age_groups,
                ticks='inside')
        ),
        polar6 = dict(
            radialaxis = dict(
                showline = False,
                gridcolor = 'white',
                showticklabels=False,
                ticks=''),
            angularaxis = dict(
                showline = False,
                gridcolor = 'white',
                tickvals=(360/len(age_groups) * np.array(range(len(age_groups)))).tolist(),
                ticktext=age_groups,
                ticks='inside')
        ),
        bargap=0.05
    )

    fig.write_image('images/report2_economic/No outbreak Immunity levels per Scenario {}.pdf'.format(reg))
    fig.show()

After further 150 days from no outbreak

In [70]:
new_colours = ['blue', 'orange', 'green', 'red', 'purple', 'deepskyblue', 'black']

trace_name = ['<b>Strategy {}</b>'.format(s+1) for s, scenario in enumerate(scenario_names)]

# Plot for each region
for r, reg in enumerate(regions):
    fig = go.Figure()
    fig = make_subplots(
        rows=int(np.ceil((len(scenario_names)-1)/3)), cols=3,
        specs=[[{'type': 'polar'}]*3]*int(np.ceil((len(scenario_names)-1)/3)),
        subplot_titles=tuple(trace_name[:-1]))
    for s, scenario in enumerate(scenario_names[:-1]):
        # Partially and fully waned
        fig.add_trace(
            go.Barpolar(
                r=np.nan_to_num(np.sqrt(waned_300_no_outbreak_outputs_percent_mean[r][s, :])),
                marker_color=['black'] * len(age_groups),
                name=trace_name[s],
                opacity=0.6,
                showlegend=False,
                text=age_groups,
                hoverinfo='text',
            ),
            row= int(np.floor(s / 3)) + 1,
            col= s % 3 + 1)

        # Recovered
        fig.add_trace(
            go.Barpolar(
                r=np.sqrt(waned_300_no_outbreak_outputs_percent_mean[r][s, :] + rec_300_no_outbreak_outputs_percent_mean[r][s, :]) -
                    np.nan_to_num(np.sqrt(waned_300_no_outbreak_outputs_percent_mean[r][s, :])),
                marker_color=['black'] * len(age_groups),
                name=trace_name[s],
                opacity=0.8,
                showlegend=False,
                text=age_groups,
                hoverinfo='text'
            ),
            row= int(np.floor(s / 3)) + 1,
            col= s % 3 + 1)

        # Recently boosted + Fully vaccinated
        fig.add_trace(
            go.Barpolar(
                r=np.sqrt(waned_300_no_outbreak_outputs_percent_mean[r][s, :] + rec_300_no_outbreak_outputs_percent_mean[r][s, :] + immune_300_no_outbreak_outputs_percent_mean[r][s, :]) -
                    np.sqrt(waned_300_no_outbreak_outputs_percent_mean[r][s, :] + rec_300_no_outbreak_outputs_percent_mean[r][s, :]),
                marker_color=[new_colours[s]] * len(age_groups),
                name=trace_name[s],
                opacity=1,
                showlegend=False,
                text=age_groups,
                hoverinfo='text'
            ),
            row= int(np.floor(s / 3)) + 1,
            col= s % 3 + 1)

        # Fully susceptible + Exposed + Infected
        fig.add_trace(
            go.Barpolar(
                r=np.sqrt(waned_300_no_outbreak_outputs_percent_mean[r][s, :] + rec_300_no_outbreak_outputs_percent_mean[r][s, :] + immune_300_no_outbreak_outputs_percent_mean[r][s, :] + susc_300_no_outbreak_outputs_percent_mean[r][s, :]) - 
                    np.sqrt(waned_300_no_outbreak_outputs_percent_mean[r][s, :] + rec_300_no_outbreak_outputs_percent_mean[r][s, :] + immune_300_no_outbreak_outputs_percent_mean[r][s, :]),
                marker_color=['gray'] * len(age_groups),
                marker_line_color='black',
                marker_line_width=2,
                name=trace_name[s],
                opacity=0.2,
                showlegend=False,
                text=age_groups,
                hoverinfo='text'
            ),
            row= int(np.floor(s / 3)) + 1,
            col= s % 3 + 1)

    fig.update_traces(text=age_groups)
    fig.update_layout(
        plot_bgcolor='white',
        title='<b>Immunity levels after 300 days for different scenarios with no outbreak for the first 150 days: {}</b>'.format(reg),
        width=1400,
        height=1300,
        template=None,
        font=dict(size=15),
        polar = dict(
            radialaxis = dict(
                showline = False,
                gridcolor = 'white',
                showticklabels=False,
                ticks=''),
            angularaxis = dict(
                showline = False,
                gridcolor = 'white',
                tickvals=(360/len(age_groups) * np.array(range(len(age_groups)))).tolist(),
                ticktext=age_groups,
                ticks='inside')
        ),
        polar2 = dict(
            radialaxis = dict(
                showline = False,
                gridcolor = 'white',
                showticklabels=False,
                ticks=''),
            angularaxis = dict(
                showline = False,
                gridcolor = 'white',
                tickvals=(360/len(age_groups) * np.array(range(len(age_groups)))).tolist(),
                ticktext=age_groups,
                ticks='inside')
        ),
        polar3 = dict(
            radialaxis = dict(
                showline = False,
                gridcolor = 'white',
                showticklabels=False,
                ticks=''),
            angularaxis = dict(
                showline = False,
                gridcolor = 'white',
                tickvals=(360/len(age_groups) * np.array(range(len(age_groups)))).tolist(),
                ticktext=age_groups,
                ticks='inside')
        ),
        polar4 = dict(
            radialaxis = dict(
                showline = False,
                gridcolor = 'white',
                showticklabels=False,
                ticks=''),
            angularaxis = dict(
                showline = False,
                gridcolor = 'white',
                tickvals=(360/len(age_groups) * np.array(range(len(age_groups)))).tolist(),
                ticktext=age_groups,
                ticks='inside')
        ),
        polar5 = dict(
            radialaxis = dict(
                showline = False,
                gridcolor = 'white',
                showticklabels=False,
                ticks=''),
            angularaxis = dict(
                showline = False,
                gridcolor = 'white',
                tickvals=(360/len(age_groups) * np.array(range(len(age_groups)))).tolist(),
                ticktext=age_groups,
                ticks='inside')
        ),
        polar6 = dict(
            radialaxis = dict(
                showline = False,
                gridcolor = 'white',
                showticklabels=False,
                ticks=''),
            angularaxis = dict(
                showline = False,
                gridcolor = 'white',
                tickvals=(360/len(age_groups) * np.array(range(len(age_groups)))).tolist(),
                ticktext=age_groups,
                ticks='inside')
        ),
        bargap=0.05
    )

    fig.write_image('images/report2_economic/Day 300 No outbreak Immunity levels per Scenario {}.pdf'.format(reg))
    fig.show()

In [71]:
trace_name = ['<b>Strategy {}</b>'.format(s+1) for s, scenario in enumerate(scenario_names)]

# Plot for each region
for r, reg in enumerate(regions):
    fig = go.Figure()
    fig = make_subplots(
        rows=1, cols=3,
        specs=[[{'type': 'polar'}]*3],
        subplot_titles=('<b>Day 0<br>No outbreak</b>', '<b>Day 150<br>Outbreak starts</b>', '<b>Day 300:<br>End of year, 150 days after start of outbreak</b>'))
    s=0
    # Day 0
    # Partially and fully waned
    fig.add_trace(
        go.Barpolar(
            r=np.nan_to_num(np.sqrt(waned_0_no_outbreak_outputs_percent_mean[r][s, :])),
            marker_color=['black'] * len(age_groups),
            name=trace_name[s],
            opacity=0.6,
            showlegend=False,
            text=age_groups,
            hoverinfo='text',
        ),
        row= 1,
        col= 1)

    # Recovered
    fig.add_trace(
        go.Barpolar(
            r=np.sqrt(waned_0_no_outbreak_outputs_percent_mean[r][s, :] + rec_0_no_outbreak_outputs_percent_mean[r][s, :]) -
                np.nan_to_num(np.sqrt(waned_0_no_outbreak_outputs_percent_mean[r][s, :])),
            marker_color=['black'] * len(age_groups),
            name=trace_name[s],
            opacity=0.8,
            showlegend=False,
            text=age_groups,
            hoverinfo='text'
        ),
        row= 1,
        col= 1)

    # Recently boosted + Fully vaccinated
    fig.add_trace(
        go.Barpolar(
            r=np.sqrt(waned_0_no_outbreak_outputs_percent_mean[r][s, :] + rec_0_no_outbreak_outputs_percent_mean[r][s, :] + immune_0_no_outbreak_outputs_percent_mean[r][s, :]) -
                np.sqrt(waned_0_no_outbreak_outputs_percent_mean[r][s, :] + rec_0_no_outbreak_outputs_percent_mean[r][s, :]),
            marker_color=[cb_colours[s]] * len(age_groups),
            name=trace_name[s],
            opacity=1,
            showlegend=False,
            text=age_groups,
            hoverinfo='text'
        ),
        row= 1,
        col= 1)

    # Fully susceptible + Exposed + Infected
    fig.add_trace(
        go.Barpolar(
            r=np.sqrt(waned_0_no_outbreak_outputs_percent_mean[r][s, :] + rec_0_no_outbreak_outputs_percent_mean[r][s, :] + immune_0_no_outbreak_outputs_percent_mean[r][s, :] + susc_0_no_outbreak_outputs_percent_mean[r][s, :]) - 
                np.sqrt(waned_0_no_outbreak_outputs_percent_mean[r][s, :] + rec_0_no_outbreak_outputs_percent_mean[r][s, :] + immune_0_no_outbreak_outputs_percent_mean[r][s, :]),
            marker_color=['gray'] * len(age_groups),
            marker_line_color='black',
            marker_line_width=2,
            name=trace_name[s],
            opacity=0.2,
            showlegend=False,
            text=age_groups,
            hoverinfo='text'
        ),
        row= 1,
        col= 1)

    # Day 150
    # Partially and fully waned
    fig.add_trace(
        go.Barpolar(
            r=np.nan_to_num(np.sqrt(waned_150_no_outbreak_outputs_percent_mean[r][s, :])),
            marker_color=['black'] * len(age_groups),
            name=trace_name[s],
            opacity=0.6,
            showlegend=False,
            text=age_groups,
            hoverinfo='text',
        ),
        row= 1,
        col= 2)

    # Recovered
    fig.add_trace(
        go.Barpolar(
            r=np.sqrt(waned_150_no_outbreak_outputs_percent_mean[r][s, :] + rec_150_no_outbreak_outputs_percent_mean[r][s, :]) -
                np.nan_to_num(np.sqrt(waned_150_no_outbreak_outputs_percent_mean[r][s, :])),
            marker_color=['black'] * len(age_groups),
            name=trace_name[s],
            opacity=0.8,
            showlegend=False,
            text=age_groups,
            hoverinfo='text'
        ),
        row= 1,
        col= 2)

    # Recently boosted + Fully vaccinated
    fig.add_trace(
        go.Barpolar(
            r=np.sqrt(waned_150_no_outbreak_outputs_percent_mean[r][s, :] + rec_150_no_outbreak_outputs_percent_mean[r][s, :] + immune_150_no_outbreak_outputs_percent_mean[r][s, :]) -
                np.sqrt(waned_150_no_outbreak_outputs_percent_mean[r][s, :] + rec_150_no_outbreak_outputs_percent_mean[r][s, :]),
            marker_color=[cb_colours[s]] * len(age_groups),
            name=trace_name[s],
            opacity=1,
            showlegend=False,
            text=age_groups,
            hoverinfo='text'
        ),
        row= 1,
        col= 2)

    # Fully susceptible + Exposed + Infected
    fig.add_trace(
        go.Barpolar(
            r=np.sqrt(waned_150_no_outbreak_outputs_percent_mean[r][s, :] + rec_150_no_outbreak_outputs_percent_mean[r][s, :] + immune_150_no_outbreak_outputs_percent_mean[r][s, :] + susc_150_no_outbreak_outputs_percent_mean[r][s, :]) - 
                np.sqrt(waned_150_no_outbreak_outputs_percent_mean[r][s, :] + rec_150_no_outbreak_outputs_percent_mean[r][s, :] + immune_150_no_outbreak_outputs_percent_mean[r][s, :]),
            marker_color=['gray'] * len(age_groups),
            marker_line_color='black',
            marker_line_width=2,
            name=trace_name[s],
            opacity=0.2,
            showlegend=False,
            text=age_groups,
            hoverinfo='text'
        ),
        row= 1,
        col= 2)
    
    # Day 300
    # Partially and fully waned
    fig.add_trace(
        go.Barpolar(
            r=np.nan_to_num(np.sqrt(waned_300_no_outbreak_outputs_percent_mean[r][s, :])),
            marker_color=['black'] * len(age_groups),
            name=trace_name[s],
            opacity=0.6,
            showlegend=False,
            text=age_groups,
            hoverinfo='text',
        ),
        row= 1,
        col= 3)

    # Recovered
    fig.add_trace(
        go.Barpolar(
            r=np.sqrt(waned_300_no_outbreak_outputs_percent_mean[r][s, :] + rec_300_no_outbreak_outputs_percent_mean[r][s, :]) -
                np.nan_to_num(np.sqrt(waned_300_no_outbreak_outputs_percent_mean[r][s, :])),
            marker_color=['black'] * len(age_groups),
            name=trace_name[s],
            opacity=0.8,
            showlegend=False,
            text=age_groups,
            hoverinfo='text'
        ),
        row= 1,
        col= 3)

    # Recently boosted + Fully vaccinated
    fig.add_trace(
        go.Barpolar(
            r=np.sqrt(waned_300_no_outbreak_outputs_percent_mean[r][s, :] + rec_300_no_outbreak_outputs_percent_mean[r][s, :] + immune_300_no_outbreak_outputs_percent_mean[r][s, :]) -
                np.sqrt(waned_300_no_outbreak_outputs_percent_mean[r][s, :] + rec_300_no_outbreak_outputs_percent_mean[r][s, :]),
            marker_color=[cb_colours[s]] * len(age_groups),
            name=trace_name[s],
            opacity=1,
            showlegend=False,
            text=age_groups,
            hoverinfo='text'
        ),
        row= 1,
        col= 3)

    # Fully susceptible + Exposed + Infected
    fig.add_trace(
        go.Barpolar(
            r=np.sqrt(waned_300_no_outbreak_outputs_percent_mean[r][s, :] + rec_300_no_outbreak_outputs_percent_mean[r][s, :] + immune_300_no_outbreak_outputs_percent_mean[r][s, :] + susc_300_no_outbreak_outputs_percent_mean[r][s, :]) - 
                np.sqrt(waned_300_no_outbreak_outputs_percent_mean[r][s, :] + rec_300_no_outbreak_outputs_percent_mean[r][s, :] + immune_300_no_outbreak_outputs_percent_mean[r][s, :]),
            marker_color=['gray'] * len(age_groups),
            marker_line_color='black',
            marker_line_width=2,
            name=trace_name[s],
            opacity=0.2,
            showlegend=False,
            text=age_groups,
            hoverinfo='text'
        ),
        row= 1,
        col= 3)

    fig.update_traces(text=age_groups)
    fig.update_layout(
        plot_bgcolor='white',
        title='<b>Immunity levels for best scenario with no outbreak for the first 150 days: {}</b>'.format(reg),
        margin=dict(t=150),
        width=1500,
        height=700,
        template=None,
        font=dict(size=15),
        polar = dict(
            radialaxis = dict(
                showline = False,
                gridcolor = 'white',
                showticklabels=False,
                ticks=''),
            angularaxis = dict(
                showline = False,
                gridcolor = 'white',
                tickvals=(360/len(age_groups) * np.array(range(len(age_groups)))).tolist(),
                ticktext=age_groups,
                ticks='inside')
        ),
        polar2 = dict(
            radialaxis = dict(
                showline = False,
                gridcolor = 'white',
                showticklabels=False,
                ticks=''),
            angularaxis = dict(
                showline = False,
                gridcolor = 'white',
                tickvals=(360/len(age_groups) * np.array(range(len(age_groups)))).tolist(),
                ticktext=age_groups,
                ticks='inside')
        ),
        polar3 = dict(
            radialaxis = dict(
                showline = False,
                gridcolor = 'white',
                showticklabels=False,
                ticks=''),
            angularaxis = dict(
                showline = False,
                gridcolor = 'white',
                tickvals=(360/len(age_groups) * np.array(range(len(age_groups)))).tolist(),
                ticktext=age_groups,
                ticks='inside')
        ),
        bargap=0.05
    )

    fig.write_image('images/report2_economic/CB Day 0-150-300 No outbreak Immunity levels per Scenario {}.pdf'.format(reg))
    fig.show()

In [72]:
new_colours = ['blue', 'orange', 'green', 'red', 'purple', 'deepskyblue', 'black']

trace_name = ['<b>Strategy {}</b>'.format(s+1) for s, scenario in enumerate(scenario_names)]

# Plot for each region
for r, reg in enumerate(regions):
    fig = go.Figure()
    fig = make_subplots(
        rows=1, cols=3,
        specs=[[{'type': 'polar'}]*3],
        subplot_titles=('<b>Day 0<br>No outbreak</b>', '<b>Day 150<br>Outbreak starts</b>', '<b>Day 300:<br>End of year, 150 days after start of outbreak</b>'))
    s=0
    # Day 0
    # Partially and fully waned
    fig.add_trace(
        go.Barpolar(
            r=np.nan_to_num(np.sqrt(waned_0_no_outbreak_outputs_percent_mean[r][s, :])),
            marker_color=['black'] * len(age_groups),
            name=trace_name[s],
            opacity=0.6,
            showlegend=False,
            text=age_groups,
            hoverinfo='text',
        ),
        row= 1,
        col= 1)

    # Recovered
    fig.add_trace(
        go.Barpolar(
            r=np.sqrt(waned_0_no_outbreak_outputs_percent_mean[r][s, :] + rec_0_no_outbreak_outputs_percent_mean[r][s, :]) -
                np.nan_to_num(np.sqrt(waned_0_no_outbreak_outputs_percent_mean[r][s, :])),
            marker_color=['black'] * len(age_groups),
            name=trace_name[s],
            opacity=0.8,
            showlegend=False,
            text=age_groups,
            hoverinfo='text'
        ),
        row= 1,
        col= 1)

    # Recently boosted + Fully vaccinated
    fig.add_trace(
        go.Barpolar(
            r=np.sqrt(waned_0_no_outbreak_outputs_percent_mean[r][s, :] + rec_0_no_outbreak_outputs_percent_mean[r][s, :] + immune_0_no_outbreak_outputs_percent_mean[r][s, :]) -
                np.sqrt(waned_0_no_outbreak_outputs_percent_mean[r][s, :] + rec_0_no_outbreak_outputs_percent_mean[r][s, :]),
            marker_color=[new_colours[s]] * len(age_groups),
            name=trace_name[s],
            opacity=1,
            showlegend=False,
            text=age_groups,
            hoverinfo='text'
        ),
        row= 1,
        col= 1)

    # Fully susceptible + Exposed + Infected
    fig.add_trace(
        go.Barpolar(
            r=np.sqrt(waned_0_no_outbreak_outputs_percent_mean[r][s, :] + rec_0_no_outbreak_outputs_percent_mean[r][s, :] + immune_0_no_outbreak_outputs_percent_mean[r][s, :] + susc_0_no_outbreak_outputs_percent_mean[r][s, :]) - 
                np.sqrt(waned_0_no_outbreak_outputs_percent_mean[r][s, :] + rec_0_no_outbreak_outputs_percent_mean[r][s, :] + immune_0_no_outbreak_outputs_percent_mean[r][s, :]),
            marker_color=['gray'] * len(age_groups),
            marker_line_color='black',
            marker_line_width=2,
            name=trace_name[s],
            opacity=0.2,
            showlegend=False,
            text=age_groups,
            hoverinfo='text'
        ),
        row= 1,
        col= 1)

    # Day 150
    # Partially and fully waned
    fig.add_trace(
        go.Barpolar(
            r=np.nan_to_num(np.sqrt(waned_150_no_outbreak_outputs_percent_mean[r][s, :])),
            marker_color=['black'] * len(age_groups),
            name=trace_name[s],
            opacity=0.6,
            showlegend=False,
            text=age_groups,
            hoverinfo='text',
        ),
        row= 1,
        col= 2)

    # Recovered
    fig.add_trace(
        go.Barpolar(
            r=np.sqrt(waned_150_no_outbreak_outputs_percent_mean[r][s, :] + rec_150_no_outbreak_outputs_percent_mean[r][s, :]) -
                np.nan_to_num(np.sqrt(waned_150_no_outbreak_outputs_percent_mean[r][s, :])),
            marker_color=['black'] * len(age_groups),
            name=trace_name[s],
            opacity=0.8,
            showlegend=False,
            text=age_groups,
            hoverinfo='text'
        ),
        row= 1,
        col= 2)

    # Recently boosted + Fully vaccinated
    fig.add_trace(
        go.Barpolar(
            r=np.sqrt(waned_150_no_outbreak_outputs_percent_mean[r][s, :] + rec_150_no_outbreak_outputs_percent_mean[r][s, :] + immune_150_no_outbreak_outputs_percent_mean[r][s, :]) -
                np.sqrt(waned_150_no_outbreak_outputs_percent_mean[r][s, :] + rec_150_no_outbreak_outputs_percent_mean[r][s, :]),
            marker_color=[new_colours[s]] * len(age_groups),
            name=trace_name[s],
            opacity=1,
            showlegend=False,
            text=age_groups,
            hoverinfo='text'
        ),
        row= 1,
        col= 2)

    # Fully susceptible + Exposed + Infected
    fig.add_trace(
        go.Barpolar(
            r=np.sqrt(waned_150_no_outbreak_outputs_percent_mean[r][s, :] + rec_150_no_outbreak_outputs_percent_mean[r][s, :] + immune_150_no_outbreak_outputs_percent_mean[r][s, :] + susc_150_no_outbreak_outputs_percent_mean[r][s, :]) - 
                np.sqrt(waned_150_no_outbreak_outputs_percent_mean[r][s, :] + rec_150_no_outbreak_outputs_percent_mean[r][s, :] + immune_150_no_outbreak_outputs_percent_mean[r][s, :]),
            marker_color=['gray'] * len(age_groups),
            marker_line_color='black',
            marker_line_width=2,
            name=trace_name[s],
            opacity=0.2,
            showlegend=False,
            text=age_groups,
            hoverinfo='text'
        ),
        row= 1,
        col= 2)
    
    # Day 300
    # Partially and fully waned
    fig.add_trace(
        go.Barpolar(
            r=np.nan_to_num(np.sqrt(waned_300_no_outbreak_outputs_percent_mean[r][s, :])),
            marker_color=['black'] * len(age_groups),
            name=trace_name[s],
            opacity=0.6,
            showlegend=False,
            text=age_groups,
            hoverinfo='text',
        ),
        row= 1,
        col= 3)

    # Recovered
    fig.add_trace(
        go.Barpolar(
            r=np.sqrt(waned_300_no_outbreak_outputs_percent_mean[r][s, :] + rec_300_no_outbreak_outputs_percent_mean[r][s, :]) -
                np.nan_to_num(np.sqrt(waned_300_no_outbreak_outputs_percent_mean[r][s, :])),
            marker_color=['black'] * len(age_groups),
            name=trace_name[s],
            opacity=0.8,
            showlegend=False,
            text=age_groups,
            hoverinfo='text'
        ),
        row= 1,
        col= 3)

    # Recently boosted + Fully vaccinated
    fig.add_trace(
        go.Barpolar(
            r=np.sqrt(waned_300_no_outbreak_outputs_percent_mean[r][s, :] + rec_300_no_outbreak_outputs_percent_mean[r][s, :] + immune_300_no_outbreak_outputs_percent_mean[r][s, :]) -
                np.sqrt(waned_300_no_outbreak_outputs_percent_mean[r][s, :] + rec_300_no_outbreak_outputs_percent_mean[r][s, :]),
            marker_color=[new_colours[s]] * len(age_groups),
            name=trace_name[s],
            opacity=1,
            showlegend=False,
            text=age_groups,
            hoverinfo='text'
        ),
        row= 1,
        col= 3)

    # Fully susceptible + Exposed + Infected
    fig.add_trace(
        go.Barpolar(
            r=np.sqrt(waned_300_no_outbreak_outputs_percent_mean[r][s, :] + rec_300_no_outbreak_outputs_percent_mean[r][s, :] + immune_300_no_outbreak_outputs_percent_mean[r][s, :] + susc_300_no_outbreak_outputs_percent_mean[r][s, :]) - 
                np.sqrt(waned_300_no_outbreak_outputs_percent_mean[r][s, :] + rec_300_no_outbreak_outputs_percent_mean[r][s, :] + immune_300_no_outbreak_outputs_percent_mean[r][s, :]),
            marker_color=['gray'] * len(age_groups),
            marker_line_color='black',
            marker_line_width=2,
            name=trace_name[s],
            opacity=0.2,
            showlegend=False,
            text=age_groups,
            hoverinfo='text'
        ),
        row= 1,
        col= 3)

    fig.update_traces(text=age_groups)
    fig.update_layout(
        plot_bgcolor='white',
        title='<b>Immunity levels for best scenario with no outbreak for the first 150 days: {}</b>'.format(reg),
        margin=dict(t=150),
        width=1500,
        height=700,
        template=None,
        font=dict(size=16),
        polar = dict(
            radialaxis = dict(
                showline = False,
                gridcolor = 'white',
                showticklabels=False,
                ticks=''),
            angularaxis = dict(
                showline = False,
                gridcolor = 'white',
                tickvals=(360/len(age_groups) * np.array(range(len(age_groups)))).tolist(),
                ticktext=age_groups,
                ticks='inside')
        ),
        polar2 = dict(
            radialaxis = dict(
                showline = False,
                gridcolor = 'white',
                showticklabels=False,
                ticks=''),
            angularaxis = dict(
                showline = False,
                gridcolor = 'white',
                tickvals=(360/len(age_groups) * np.array(range(len(age_groups)))).tolist(),
                ticktext=age_groups,
                ticks='inside')
        ),
        polar3 = dict(
            radialaxis = dict(
                showline = False,
                gridcolor = 'white',
                showticklabels=False,
                ticks=''),
            angularaxis = dict(
                showline = False,
                gridcolor = 'white',
                tickvals=(360/len(age_groups) * np.array(range(len(age_groups)))).tolist(),
                ticktext=age_groups,
                ticks='inside')
        ),
        bargap=0.05
    )

    fig.write_image('images/report2_economic/Day 0-150-300 No outbreak Immunity levels per Scenario {}.pdf'.format(reg))
    fig.show()

In [73]:
new_regions = ['UK'] + regions[1:]

trace_name = ['Scenario {}'.format(s+1) for s, scenario in enumerate(scenario_names[:-1])] + [scenario_names[-1]]

fig = go.Figure()
# Plot for each region
for s, scenario in enumerate(scenario_names):
    fig.add_trace(
        go.Bar(
            y=[np.sum(_150_no_outbreak_total_deaths_mean[r][s, :] + _300_no_outbreak_total_deaths_mean[r][s, :]) for r, reg in enumerate(regions)],
            x=new_regions,
            name=trace_name[s],
            marker_color=cb_colours[s],
        )
    )

# Add axis labels
fig.update_layout(
    boxmode='group',
    title='Mean deaths per 100,000 for different countries and scenarios from {} simulations'.format(len(regimes)),
    width=1150,
    height=575,
    plot_bgcolor='white',
    font=dict(
            size=16),
    xaxis=dict(linecolor='black'),
    yaxis=dict(
        linecolor='black',
        title='Deaths (per 100k)'),
    hovermode='x unified',
    legend=dict(
            orientation="h",
            yanchor="bottom",
            y=0.88,
            xanchor="right",
            x=1.0000001,
            bordercolor="Black",
            borderwidth=1
        )
    )

fig.write_image('images/report2_economic/CB Day 300 No outbreak Deaths per Scenario and Country.pdf')
fig.show()

In [74]:
new_colours = ['blue', 'orange', 'green', 'red', 'purple', 'deepskyblue', 'black']

trace_name = ['Scenario {}'.format(s+1) for s, scenario in enumerate(scenario_names[:-1])] + [scenario_names[-1]]

fig = go.Figure()
# Plot for each region
for s, scenario in enumerate(scenario_names):
    fig.add_trace(
        go.Bar(
            y=[np.sum(_150_no_outbreak_total_years_of_life_lost_mean[r][s, :] + _300_no_outbreak_total_years_of_life_lost_mean[r][s, :]) for r, reg in enumerate(regions)],
            x=regions,
            name=trace_name[s],
            marker_color=new_colours[s],
        )
    )

# Add axis labels
fig.update_layout(
    boxmode='group',
    title='Mean years of Life Lost per 100,000 for different countries and scenarios from {} simulations'.format(len(regimes)),
    width=1000,
    height=500,
    plot_bgcolor='white',
    xaxis=dict(linecolor='black'),
    yaxis=dict(linecolor='black'),
    hovermode='x unified',
    legend=dict(
            orientation="h",
            yanchor="bottom",
            y=0.88,
            xanchor="right",
            x=1.0000001,
            bordercolor="Black",
            borderwidth=1
        )
    )

fig.write_image('images/report2_economic/Day 300 No outbreak Years of Life Lost per Scenario and Country.pdf')
fig.show()